<a href="https://colab.research.google.com/github/run-llama/llama_index/blob/main/docs/docs/examples/cookbooks/GraphRAG_v1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


The structure of this notebook is based on the LlamaIndex GraphRAG framework, which has been extended and enhanced in several key areas. We built upon the original codebase to implement entity-relation extraction and knowledge graph creation, incorporating citation handling, modified data parsing, advanced prompt engineering, and improvements for visualization and community building. Additionally, we refined the generation pipeline by incorporating a local search mechanism using embedding-based retrieval, selecting only the top community summaries as context for final answer generation.

# GraphRAG Implementation with LlamaIndex

[GraphRAG (Graphs + Retrieval Augmented Generation)](https://www.microsoft.com/en-us/research/project/graphrag/) combines the strengths of Retrieval Augmented Generation (RAG) and Query-Focused Summarization (QFS) to effectively handle complex queries over large text datasets. While RAG excels in fetching precise information, it struggles with broader queries that require thematic understanding, a challenge that QFS addresses but cannot scale well. GraphRAG integrates these approaches to offer responsive and thorough querying capabilities across extensive, diverse text corpora.


This notebook provides guidance on constructing the GraphRAG pipeline using the LlamaIndex PropertyGraph abstractions.


**NOTE:** This is an approximate implementation of GraphRAG. We are currently developing a series of cookbooks that will detail the exact implementation of GraphRAG.

## GraphRAG Aproach

The GraphRAG involves two steps:

1. Graph Generation - Creates Graph, builds communities and its summaries over the given document.
2. Answer to the Query - Use summaries of the communities created from step-1 to answer the query.

**Graph Generation:**

1. **Source Documents to Text Chunks:** Source documents are divided into smaller text chunks for easier processing.

2. **Text Chunks to Element Instances:** Each text chunk is analyzed to identify and extract entities and relationships, resulting in a list of tuples that represent these elements.

3. **Element Instances to Element Summaries:** The extracted entities and relationships are summarized into descriptive text blocks for each element using the LLM.

4. **Element Summaries to Graph Communities:** These entities, relationships and summaries form a graph, which is subsequently partitioned into communities using algorithms using Heirarchical Leiden to establish a hierarchical structure.

5. **Graph Communities to Community Summaries:** The LLM generates summaries for each community, providing insights into the dataset’s overall topical structure and semantics.

**Answering the Query:**

**Community Summaries to Global Answers:** The summaries of the communities are utilized to respond to user queries. This involves generating intermediate answers, which are then consolidated into a comprehensive global answer.


## GraphRAG Pipeline Components

Here are the different components we implemented to build all of the processes mentioned above.

1. **Source Documents to Text Chunks:** Implemented using `SentenceSplitter` with a chunk size of 1024 and chunk overlap of 20 tokens.

2. **Text Chunks to Element Instances AND Element Instances to Element Summaries:** Implemented using `GraphRAGExtractor`.

3. **Element Summaries to Graph Communities AND Graph Communities to Community Summaries:** Implemented using `GraphRAGStore`.

4. **Community Summaries to Global Answers:** Implemented using `GraphQueryEngine`.


Let's check into each of these components and build GraphRAG pipeline.


## Installation

`graspologic` is used to use hierarchical_leiden for building communities.

In [ ]:
!pip install llama-index graspologic numpy==1.24.4 scipy==1.12.0

In [ ]:
!pip install pyvis

In [ ]:
!pip install llama-index-llms-groq

In [ ]:
!pip install llama_index.embeddings.huggingface

In [ ]:
!pip install ipdb #debugger

In [ ]:
!huggingface-cli login # for llama tokenizer

# API Keys

In [ ]:
api_key_groq="" ## api key for groq

In [ ]:
huggingface_token = "" # for llama tokenizer

## Load Data

We will use a sample news article dataset retrieved from Diffbot, which Tomaz has conveniently made available on GitHub for easy access.

The dataset contains 2,500 samples; for ease of experimentation, we will use 50 of these samples, which include the `title` and `text` of news articles.

In [ ]:
import pandas as pd
from llama_index.core import Document

news = pd.read_csv(
    "/content/cv_nlp_ml_2023-2024_cleaned_142k.csv"
)

news.head()

<ipython-input-5-c807fa7e1865>:4: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  news = pd.read_csv(


Unnamed: 0         id                                            authors  \
0       76653   808.0521            Ian Pratt-Hartmann and Lawrence S. Moss   
1      104832    901.359                          Chunhua Shen and Hanxi Li   
2      109646    902.343  Yishay Mansour, Mehryar Mohri, Afshin Rostamiz...   
3      169585  1001.4297  Andrew D. Straw, Kristin Branson, Titus R. Neu...   
4      200263  1007.1025                                      Henryk Fuk\'s   

                                               title  \
0              Logics for the Relational Syllogistic   
1     On the Dual Formulation of Boosting Algorithms   
2  Domain Adaptation: Learning Bounds and Algorithms   
3  Multi-camera Realtime 3D Tracking of Multiple ...   
4  Inflection system of a language as a complex n...   

                                            abstract update_date  year  
0    The Aristotelian syllogistic cannot account ...  2024-04-24  2024  
1    We study boosting algorithms from a new pers...  2023-05-30  2023  
2    This paper addresses the general problem of ...  2023-12-04  2023  
3    Automated tracking of animal movement allows...  2023-02-01  2023  
4    We investigate inflection structure of a syn...  2023-12-18  2023

In [ ]:
news['id'] = news['id'].astype(str)

In [ ]:
filtered_data = news[news['id'].astype(str).str.startswith('2410.1307')]
filtered_data

Unnamed: 0          id  \
138540     2171271  2410.13070   
138541     2171274  2410.13073   
138542     2171278  2410.13077   

                                                  authors  \
138540                  Renyi Qu, Ruixuan Tu, Forrest Bao   
138541  Ximing Dong, Shaowei Wang, Dayi Lin, Gopi Kris...   
138542                           Haoyan Luo, Lucia Specia   

                                                    title  \
138540  Is Semantic Chunking Worth the Computational C...   
138541  PromptExp: Multi-granularity Prompt Explanatio...   
138542  Tuning Language Models by Mixture-of-Depths En...   

                                                 abstract update_date  year  
138540    Recent advances in Retrieval-Augmented Gener...  2024-10-18  2024  
138541    Large Language Models excel in tasks like na...  2024-10-31  2024  
138542    Transformer-based Large Language Models (LLM...  2024-10-18  2024

In [ ]:
filtered_data.to_csv("/content/paper_ids_and_titles_RAG(in).csv")

In [ ]:
news.columns

Index(['Unnamed: 0', 'id', 'authors', 'title', 'abstract', 'update_date',
       'year'],
      dtype='object')

# Prepare documents as required by LlamaIndex

In [ ]:
news.dtypes

Unnamed: 0      int64
id             object
authors        object
title          object
abstract       object
update_date    object
year            int64
dtype: object

In [ ]:
selected_papers=pd.read_csv('/content/paper_ids_and_titles_RAG(in).csv')

In [ ]:
selected_paper_ids= selected_papers['id']
print(len(selected_papers))

100


In [ ]:
list(selected_papers.id)

[2410.1307, 2410.13073, 2410.13077]

In [ ]:
data = news[news['id'].isin(list(selected_papers.id.astype(str)))]
print(data.shape)
data.head()

(99, 7)


Unnamed: 0          id  \
3086      1489281  2106.11517   
50610     1888371  2308.00479   
55554     1905909  2309.01105   
55656     1906235  2309.01431   
59374     1920021  2309.15217   

                                                 authors  \
3086   Shamane Siriwardhana, Rivindu Weerasekera, Ell...   
50610           S. S. Manathunga and Y. A. Illangasekara   
55554                                      Cheonsu Jeong   
55656       Jiawei Chen, Hongyu Lin, Xianpei Han, Le Sun   
59374  Shahul Es, Jithin James, Luis Espinosa-Anke, S...   

                                                   title  \
3086   Fine-tune the Entire RAG Architecture (includi...   
50610  Retrieval Augmented Generation and Representat...   
55554  A Study on the Implementation of Generative AI...   
55656  Benchmarking Large Language Models in Retrieva...   
59374  RAGAS: Automated Evaluation of Retrieval Augme...   

                                                abstract update_date  year  
3086     In this paper, we illustrate how to fine-tun...  2024-10-08  2024  
50610    Large Language Models are increasingly being...  2023-08-02  2023  
55554    This study presents a method for implementin...  2024-01-03  2024  
55656    Retrieval-Augmented Generation (RAG) is a pr...  2023-12-21  2023  
59374    We introduce RAGAs (Retrieval Augmented Gene...  2023-09-28  2023

In [ ]:
data.to_csv("/content/graphrag_data.csv")

In [ ]:
data[['title','abstract']].to_csv("/content/graphrag_data_title_abstract.csv")

In [ ]:
for id in selected_papers.id.astype(str):
  if id not in data.id.values:
    print(id)

2404.00657
2106.11517
2309.15217
2407.21059
2402.19473
2405.07437
2405.13002
2309.01105
2407.13193
2403.05676
2407.19794
2408.07425
2409.05591
2405.00175
2401.07883
2408.08067
2405.06211
2410.1307
2408.02545
2312.10997
2407.01219
2405.13576
2401.14887
2404.10981
2407.16833
2406.13249
2405.12363
2407.00361
2406.14972
2401.17043
2403.0082
2407.01102
2403.10081
2402.16874
2405.1642
2408.01262
2403.1545
2401.06954
2308.00479
2409.01666
2401.15884
2403.0904
2406.05085
2409.09916
2408.04259
2407.15353
2406.07348
2406.16828
2406.12881
2408.08921
2406.11424
2404.08189
2404.19543
2409.03171
2408.05141
2405.19519
2404.07221
2309.01431
2407.11005
2409.11279
2406.13213
2409.05152
2407.03955
2407.21055
2407.08223
2404.01037
2406.11201
2402.01767
2404.02103
2405.16178
2406.03963
2404.02835
2408.13533
2404.12457
2405.1967
2407.12057
2404.0061
2406.16167
2403.15729
2403.11413
2405.01359


In [ ]:
documents = [
    Document(text=f"{(row['title'], row['authors'])}: {row['abstract']}", metadata={"paper_id": str(row['id'])})
    for i, row in data.iterrows()
]

In [ ]:
print(documents[-1])

Doc ID: a5620310-117b-4c49-a638-c2f38c8d74fc
Text: ('AutoRAG: Automated Framework for optimization of Retrieval
Augmented\n  Generation Pipeline', 'Dongkyu Kim, Byoungwook Kim,
Donggeon Han and Matou\\v{s} Eibich'):   Using LLMs (Large Language
Models) in conjunction with external documents has made RAG
(Retrieval-Augmented Generation) an essential technology. Numerous
techniques and modules for...


In [ ]:
print(len(documents))

99


## Setup LLM and encoder


In [ ]:
def completion_to_prompt(completion):
   return f"<|im_start|>system\n<|im_end|>\n<|im_start|>user\n{completion}<|im_end|>\n<|im_start|>assistant\n"

def messages_to_prompt(messages):
    prompt = ""
    for message in messages:
        if message.role == "system":
            prompt += f"<|im_start|>system\n{message.content}<|im_end|>\n"
        elif message.role == "user":
            prompt += f"<|im_start|>user\n{message.content}<|im_end|>\n"
        elif message.role == "assistant":
            prompt += f"<|im_start|>assistant\n{message.content}<|im_end|>\n"

    if not prompt.startswith("<|im_start|>system"):
        prompt = "<|im_start|>system\n" + prompt

    prompt = prompt + "<|im_start|>assistant\n"

    return prompt

import torch
from llama_index.core import Settings
from llama_index.core.node_parser import SentenceSplitter
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.llms.groq import Groq

llm = Groq(model="llama3-8b-8192", api_key=api_key_groq)

# Set embedding model
Settings.embed_model = HuggingFaceEmbedding(
    model_name = "allenai/scibert_scivocab_uncased"
)

# Set the size of the text chunk for retrieval
Settings.transformations = [SentenceSplitter(chunk_size=1024)]


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/385 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/442M [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/228k [00:00<?, ?B/s]

In [ ]:
print(llm)

callback_manager=<llama_index.core.callbacks.base.CallbackManager object at 0x7e8b432dc850> system_prompt=None messages_to_prompt=<function messages_to_prompt at 0x7e8b46412e60> completion_to_prompt=<function default_completion_to_prompt at 0x7e8b464c00d0> output_parser=None pydantic_program_mode=<PydanticProgramMode.DEFAULT: 'default'> query_wrapper_prompt=None model='llama3-8b-8192' temperature=0.1 max_tokens=None logprobs=None top_logprobs=0 additional_kwargs={} max_retries=3 timeout=60.0 default_headers=None reuse_client=True api_key='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' api_base='https://api.groq.com/openai/v1' api_version='' strict=False context_window=3900 is_chat_model=True is_function_calling_model=True tokenizer=None


## GraphRAGExtractor

The GraphRAGExtractor class is designed to extract triples (subject-relation-object) from text and enrich them by adding descriptions for entities and relationships to their properties using an LLM.

This functionality is similar to that of the `SimpleLLMPathExtractor`, but includes additional enhancements to handle entity, relationship descriptions. For guidance on implementation, you may look at similar existing [extractors](https://docs.llamaindex.ai/en/latest/examples/property_graph/Dynamic_KG_Extraction/?h=comparing).

Here's a breakdown of its functionality:

**Key Components:**

1. `llm:` The language model used for extraction.
2. `extract_prompt:` A prompt template used to guide the LLM in extracting information.
3. `parse_fn:` A function to parse the LLM's output into structured data.
4. `max_paths_per_chunk:` Limits the number of triples extracted per text chunk.
5. `num_workers:` For parallel processing of multiple text nodes.


**Main Methods:**

1. `__call__:` The entry point for processing a list of text nodes.
2. `acall:` An asynchronous version of __call__ for improved performance.
3. `_aextract:` The core method that processes each individual node.


**Extraction Process:**

For each input node (chunk of text):
1. It sends the text to the LLM along with the extraction prompt.
2. The LLM's response is parsed to extract entities, relationships, descriptions for entities and relations.
3. Entities are converted into EntityNode objects. Entity description is stored in metadata
4. Relationships are converted into Relation objects. Relationship description is stored in metadata.
5. These are added to the node's metadata under KG_NODES_KEY and KG_RELATIONS_KEY.


In [ ]:
import asyncio
import nest_asyncio

nest_asyncio.apply()
import time

from typing import Any, List, Callable, Optional, Union, Dict
from IPython.display import Markdown, display

from llama_index.core.async_utils import run_jobs
from llama_index.core.indices.property_graph.utils import (
    default_parse_triplets_fn,
)
from llama_index.core.graph_stores.types import (
    EntityNode,
    KG_NODES_KEY,
    KG_RELATIONS_KEY,
    Relation,
)
from llama_index.core.llms.llm import LLM
from llama_index.core.prompts import PromptTemplate
from llama_index.core.prompts.default_prompts import (
    DEFAULT_KG_TRIPLET_EXTRACT_PROMPT,
)
from llama_index.core.schema import TransformComponent, BaseNode
from llama_index.core.bridge.pydantic import BaseModel, Field

global count_error
count_error = 0
class GraphRAGExtractor(TransformComponent):
    """Extract triples from a graph.

    Uses an LLM and a simple prompt + output parsing to extract paths (i.e. triples) and entity, relation descriptions from text.

    Args:
        llm (LLM):
            The language model to use.
        extract_prompt (Union[str, PromptTemplate]):
            The prompt to use for extracting triples.
        parse_fn (callable):
            A function to parse the output of the language model.
        num_workers (int):
            The number of workers to use for parallel processing.
        max_paths_per_chunk (int):
            The maximum number of paths to extract per chunk.
    """

    llm: LLM
    extract_prompt: PromptTemplate
    parse_fn: Callable
    num_workers: int
    max_paths_per_chunk: int

    def __init__(
        self,
        llm: Optional[LLM] = None,
        extract_prompt: Optional[Union[str, PromptTemplate]] = None,
        parse_fn: Callable = default_parse_triplets_fn,
        max_paths_per_chunk: int = 10,
        num_workers: int = 4,

    ) -> None:
        """Init params."""
        from llama_index.core import Settings

        if isinstance(extract_prompt, str):
            from llama_index.core.prompts.base import PromptTemplate
            from llama_index.core.prompts.prompt_type import PromptType

            extract_prompt = PromptTemplate(extract_prompt, prompt_type=PromptType.QUESTION_ANSWER)
            # print(extract_prompt)

        super().__init__(
            llm=llm or Settings.llm,
            extract_prompt=extract_prompt or DEFAULT_KG_TRIPLET_EXTRACT_PROMPT,
            parse_fn=parse_fn,
            num_workers=num_workers,
            max_paths_per_chunk=max_paths_per_chunk,
        )

    @classmethod
    def class_name(cls) -> str:
        return "GraphExtractor"

    def __call__(
        self, nodes: List[BaseNode], show_progress: bool = False, **kwargs: Any
    ) -> List[BaseNode]:
        """Extract triples from nodes."""
        return asyncio.run(
            self.acall(nodes, show_progress=show_progress, **kwargs)
        )

    async def _aextract(self, node: BaseNode) -> BaseNode:
        """Extract triples from a node."""
        assert hasattr(node, "text")
        text = node.get_content(metadata_mode="llm")
        try:
            time.sleep(0.5)
            llm_response = await self.llm.apredict(
                self.extract_prompt,
                text=text,
                max_knowledge_triplets=self.max_paths_per_chunk,
            )

            entities, entities_relationship = self.parse_fn(llm_response)
        except ValueError:
            global count_error
            count_error += 1
            entities = []
            entities_relationship = []

        existing_nodes = node.metadata.pop(KG_NODES_KEY, [])
        existing_relations = node.metadata.pop(KG_RELATIONS_KEY, [])
        metadata = node.metadata.copy()
        for entity, entity_type, description in entities:
            metadata[
                "entity_description"
            ] = description
            entity_node = EntityNode(
                name=entity, label=entity_type, properties=metadata
            )
            # the properties holds metadata
            existing_nodes.append(entity_node)

        metadata = node.metadata.copy()
        for triple in entities_relationship:
            subj, rel, obj, description = triple
            subj_node = EntityNode(name=subj, properties=metadata)
            obj_node = EntityNode(name=obj, properties=metadata)
            metadata["relationship_description"] = description
            rel_node = Relation(
                label=rel,
                source_id=subj_node.id,
                target_id=obj_node.id,
                properties=metadata,
            )

            existing_nodes.extend([subj_node, obj_node])
            existing_relations.append(rel_node)

        node.metadata[KG_NODES_KEY] = existing_nodes
        node.metadata[KG_RELATIONS_KEY] = existing_relations
        return node

    async def acall(
        self, nodes: List[BaseNode], show_progress: bool = False, **kwargs: Any
    ) -> List[BaseNode]:
        """Extract triples from nodes async."""
        jobs = []
        for node in nodes:
            jobs.append(self._aextract(node))

        return await run_jobs(
            jobs,
            workers=self.num_workers,
            show_progress=show_progress,
            desc="Extracting paths from text",
        )

## GraphRAGStore

The `GraphRAGStore` class is an extension of the `SimplePropertyGraphStore `class, designed to implement GraphRAG pipeline. Here's a breakdown of its key components and functions:


The class uses community detection algorithms to group related nodes in the graph and then it generates summaries for each community using an LLM.


**Key Methods:**

`build_communities():`

1. Converts the internal graph representation to a NetworkX graph.

2. Applies the hierarchical Leiden algorithm for community detection.

3. Collects detailed information about each community.

4. Generates summaries for each community.

`generate_community_summary(text):`

1. Uses LLM to generate a summary of the relationships in a community.
2. The summary includes entity names and a synthesis of relationship descriptions.

`_create_nx_graph():`

1. Converts the internal graph representation to a NetworkX graph for community detection.

`_collect_community_info(nx_graph, clusters):`

1. Collects detailed information about each node based on its community.
2. Creates a string representation of each relationship within a community.

`_summarize_communities(community_info):`

1. Generates and stores summaries for each community using LLM.

`get_community_summaries():`

1. Returns the community summaries by building them if not already done.

In [ ]:
COMMUNITY_SUMMARY_PROMPT = "You are provided with a set of relationships from a knowledge graph, each represented as "
                    "entity1->entity2->paper_id->relation->relationship_description. Your task is to create a summary of these "
                    "relationships. The summary should include the names of the entities involved and a concise synthesis "
                    "of the relationship descriptions. The goal is to capture the most critical and relevant details that "
                    "highlight the nature and significance of each relationship. Ensure that the summary is coherent and "
                    "integrates the information in a way that emphasizes the key aspects of the relationships. "
                    "End with the paper_ids from each knowledge graph by including them as a list in paranthesis."

COMMUNITY_SUMMARY_PROMPT_ALTERNATIVE = "You are an expert knowledge graph analyst tasked with synthesizing complex entity relationships. "
                    "When generating the community summary, follow these comprehensive guidelines:\n\n"
                    "1. Relationship Analysis:\n"
                    "   - Identify and categorize the types of relationships between entities\n"
                    "   - Highlight the most significant and recurring relationship patterns\n"
                    "   - Capture the semantic meaning and context of each relationship\n\n"
                    "2. Comprehensive Synthesis:\n"
                    "   - Create a coherent narrative that explains the interconnections\n"
                    "   - Provide insights into how different entities are linked\n"
                    "   - Emphasize the broader implications of these relationships\n\n"
                    "3. Structural Approach:\n"
                    "   - Organize the summary with clear sections:\n"
                    "     a) Key Entities Overview\n"
                    "     b) Relationship Dynamics\n"
                    "     c) Significant Interconnections\n\n"
                    "4. Detailed Considerations:\n"
                    "   - Extract nuanced details from relationship descriptions\n"
                    "   - Identify potential themes or research directions\n"
                    "   - Maintain a balance between specificity and broader context\n\n"
                    "Formatting Requirements:\n"
                    "- Provide a concise yet comprehensive summary (200-400 words)\n"
                    "- Use clear, scholarly language\n"
                    "- End with a list of unique paper IDs in parentheses\n\n"
                    "Input Format: entity1 -> entity2 -> paper_id -> relation -> relationship_description. "
                    "If the community is mainly a connection of entities such as authors, which does not have much concrete context and information, feel free to write a short summary. "
                    "Otherwisee, be detailed in capturing the essence, specifics, and technical knowledge from the community."
                    "The summary must thoroughly reflect and capture specific and technical knowledge represented in the given text."

In [ ]:
import re
from llama_index.core.graph_stores import SimplePropertyGraphStore
import networkx as nx
from graspologic.partition import hierarchical_leiden

from llama_index.core.llms import ChatMessage
from collections import defaultdict

class GraphRAGStore(SimplePropertyGraphStore):
    community_summary = {}
    max_cluster_size = 15
    community_mapping={}
    nx_graph= None
    entity_info = None
    cluster = None
    llm=llm


    def generate_community_summary(self, text):
        """Generate summary for a given text using an LLM."""
        messages = [
            ChatMessage(
                role="system",
                content=(
                    COMMUNITY_SUMMARY_PROMPT
                ),
            ),
            ChatMessage(role="user", content=text),
        ]
        # import ipdb; ipdb.set_trace()
        response = llm.chat(messages)
        clean_response = re.sub(r"^assistant:\s*", "", str(response)).strip()
        return clean_response

    def build_communities(self):
        """Builds communities from the graph and summarizes them."""
        print("\n LLM currently used: ", llm)
        nx_graph = self._create_nx_graph()
        self.nx_graph= nx_graph
        community_hierarchical_clusters = hierarchical_leiden(
            nx_graph, max_cluster_size=self.max_cluster_size
        )
        self.cluster= community_hierarchical_clusters
        self.entity_info, community_info = self._collect_community_info(
            nx_graph, community_hierarchical_clusters
        )
        self._summarize_communities(community_info)
        # self.visualize_community_graph()

    def _create_nx_graph(self):
        """Converts internal graph representation to NetworkX graph."""
        nx_graph = nx.Graph()
        for node in self.graph.nodes.values():
            nx_graph.add_node(str(node), **{'paper_id': node.properties['paper_id']})
            # print(str(node))
            # import ipdb; ipdb.set_trace()
        for relation in self.graph.relations.values():

            nx_graph.add_edge(
                relation.source_id,
                relation.target_id,
                relationship=relation.label,
                description=relation.properties["relationship_description"],
                paper_id=relation.properties["paper_id"] ############################ modification -> adding paper id information
            )
        return nx_graph

    def _collect_community_info(self, nx_graph, clusters):
        """Collect detailed information for each node based on their community."""

        print("CLUSTERS:  \n", clusters)
        entity_info = defaultdict(set)
        community_info = {}

        for item in clusters:
            node = item.node
            cluster_id = item.cluster

            # Update entity_info
            entity_info[node].add(cluster_id)
            if cluster_id not in community_info:
                community_info[cluster_id] = {"detail":[], "paper_ids":[]}
            for neighbor in nx_graph.neighbors(node):
                edge_data = nx_graph.get_edge_data(node, neighbor)
                if edge_data:
                    # ensure that the paper id is included in the community summary since the LLMs make use of this during answer generation and can help improve referencing
                    detail = f"{node} -> {neighbor} -> {edge_data['paper_id'] }-> {edge_data['relationship']} -> {edge_data['description']}"
                    community_info[cluster_id]['detail'].append(detail)
                    community_info[cluster_id]['paper_ids'].append(edge_data.get("paper_id",""))

        # Convert sets to lists for easier serialization if needed
        community_mapping = {item.node: item.cluster for item in clusters}
        self.community_mapping= community_mapping
        print("Community Mapping (_collect_community_info):", community_mapping)
        entity_info = {k: list(v) for k, v in entity_info.items()}
        return dict(entity_info), dict(community_info)


    def _summarize_communities(self, community_info):
        """Generate and store summaries for each community."""
        for community_id, details in community_info.items():
            details_text = (
                "\n".join(details["detail"]) + "."
            )  # Ensure it ends with a period
            print(f"details: {details_text}")
            # ids = details['paper_ids']
            self.community_summary[
                community_id
            ] = {"summary": self.generate_community_summary(details_text), "paper_ids": details["paper_ids"]}

        print(f"Community summaries: {self.community_summary}")


    def get_community_summaries(self):
        """Returns the community summaries, building them if not already done."""
        if not self.community_summary:
            self.build_communities()
        return self.community_summary

    def visualize_community_graph(self):
      """Visualize the graph with community-based coloring and detailed node information."""
      from pyvis.network import Network

      # Create a NetworkX graph from the stored graph representation
      nx_graph = self.nx_graph
      # print("\n\n CLUSTERS: ", self.clusters)
      # Initialize PyVis network
      net = Network(notebook=False, height="750px", width="100%", directed=False)

      # Map each node to its community
      community_mapping = self.community_mapping
      # print("\n\n COMMUNITY MAPPING", community_mapping)

      # Generate colors for each community
      import matplotlib.pyplot as plt
      num_communities = len(set(community_mapping.values()))
      color_map = plt.cm.get_cmap("hsv", num_communities)
      community_colors = {}
      color_threshold = 0.25  # Adjust this to control how "different" RGB values must be
      # num_communities = len(color_map.colors)

      for cluster_id, (r, g, b, _) in zip(range(num_communities), color_map(np.linspace(0, 1, num_communities))):
          # Avoid shades of grey by ensuring RGB values are not too close
          if abs(r - g) < color_threshold and abs(g - b) < color_threshold and abs(b - r) < color_threshold:
              # If it's grey-like, skip or adjust to a random vibrant color
              continue

          community_colors[cluster_id] = f"#{int(255 * r):02x}{int(255 * g):02x}{int(255 * b):02x}"

      # Add nodes with community colors and metadata
      for node, data in nx_graph.nodes(data=True):
          print(f"\n\n Printing from Viz\n Node: {node}, Data: {data}")
          community_id = community_mapping.get(node, -1)
          color = community_colors.get(community_id, "#cccccc")  # Default to gray if no community
          title = f"Node: {node}\n"
          import ipdb; ipdb.set_trace()
          title += f"<Paper ID: { node.properties['paper_id']}<br>"
          title += f"<b>Community:</b> {community_id}<br>"
          title += f"<b>Descriptions:</b> {', '.join(data.get('descriptions', []))}<br>"

          net.add_node(
              node,
              label=node,
              title=title,
              color=color
          )

      # Add edges with metadata
      for u, v, data in nx_graph.edges(data=True):
          import ipdb; ipdb.set_trace()
          title = f"<b>Relationship:</b> {data.get('relationship', 'N/A')}<br>"
          title += f"<b>Description:</b> {data.get('description', 'N/A')}<br>"
          title += f"<b>Paper ID:</b> {data.get('paper_id', 'N/A')}<br>"

          net.add_edge(
              u,
              v,
              title=title
          )


      # import ipdb; ipdb.set_trace()
      # print(net)
      # Show the graph
      # net.show("community_graph.html")
      net.save_graph("graph_visualization.html")
      print("Community graph visualization saved as 'graph_visualization.html'")

## GraphRAGQueryEngine

The GraphRAGQueryEngine class is a custom query engine designed to process queries using the GraphRAG approach. It leverages the community summaries generated by the GraphRAGStore to answer user queries. Here's a breakdown of its functionality:

**Main Components:**

`graph_store:` An instance of GraphRAGStore, which contains the community summaries.
`llm:` A Language Model (LLM) used for generating and aggregating answers.


**Key Methods:**

`custom_query(query_str: str)`

1. This is the main entry point for processing a query. It retrieves community summaries, generates answers from each summary, and then aggregates these answers into a final response.

`generate_answer_from_summary(community_summary, query):`

1. Generates an answer for the query based on a single community summary.
Uses the LLM to interpret the community summary in the context of the query.

`aggregate_answers(community_answers):`

1. Combines individual answers from different communities into a coherent final response.
2. Uses the LLM to synthesize multiple perspectives into a single, concise answer.


**Query Processing Flow:**

1. Retrieve community summaries from the graph store.
2. For each community summary, generate a specific answer to the query.
3. Aggregate all community-specific answers into a final, coherent response.


**Example usage:**

```
query_engine = GraphRAGQueryEngine(graph_store=graph_store, llm=llm)

response = query_engine.query("query")
```

In [ ]:
from transformers import AutoTokenizer

# Load tokenizer
tokenizer = AutoTokenizer.from_pretrained("meta-llama/Meta-Llama-3-8B")

tokenizer_config.json:   0%|          | 0.00/50.6k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/73.0 [00:00<?, ?B/s]

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


Number of tokens: 135


In [ ]:
FINAL_ANSWER_PROMPT = """You are an academic researcher who combines your existing knowledge with provided context to write a targeted literature review.
          Core Instructions:
          - Use only directly relevant context
          - Synthesize with analytical depth
          - Provide critical insights
          - Avoid repetition
          - Cite paper ids precisely

          Critical Requirements:
          - Extract nuanced research insights
          - Connect ideas coherently
          - Demonstrate scholarly understanding
          - Prioritize quality over quantity
          You are an expert researcher who:
        - Aggregates complex information precisely
        - Writes with academic rigor
        - Uses only contextually relevant information
        - Produces analytically rich, concise syntheses.
        - Writes the final response as paragraphs, not sections.
        """
FINAL_ANSWER_CHAT_PROMPT = f"""
Here is the information given in the form of (intermediate answer, paper_ids): {community_answers}. Only discuss topics that are relevant to the query, do not mention or contrast with topics not relevant to the query in any capacity. Also do not start with conversational piece or mention 'community summaries' Provide in-text citations through the paper ids and map them to a references section that contains paper ids and paper titles."""

In [ ]:
from llama_index.core.query_engine import CustomQueryEngine
from llama_index.core.llms import LLM
from llama_index.core import PropertyGraphIndex


class GraphRAGQueryEngine(CustomQueryEngine):
    graph_store: GraphRAGStore
    llm: LLM
    index: PropertyGraphIndex
    similarity_top_k: int = 20

    def custom_query(self, query_str: str) -> str:
        """Process all community summaries to generate answers to a specific query."""
        # import ipdb; ipdb.set_trace()
        entities = self.get_entities(query_str, self.similarity_top_k)

        community_ids = self.retrieve_entity_communities(
            self.graph_store.entity_info, entities
        )

        community_summaries = self.graph_store.get_community_summaries()

        community_answers = [
            self.generate_answer_from_summary(community_summary, query_str)
            for id, community_summary in community_summaries.items()
            if id in community_ids
        ]

        community_answers = [x for x in community_answers if x is not None]
        # import ipdb; ipdb.set_trace()
        num_answers = self.calculate_tokens(community_answers)
        final_answer = self.aggregate_answers(community_answers[0:num_answers])

        return final_answer

    def get_entities(self, query_str, similarity_top_k):

        # import ipdb; ipdb.set_trace()
        # nodes are neaturally returned in a descending order of similarity which is good.
        nodes_retrieved = self.index.as_retriever(
            retriever_mode="embedding",
            similarity_top_k=similarity_top_k
        ).retrieve(query_str)
        # import ipdb; ipdb.set_trace()
        entities = set()
        alist = []
        pattern = r"(\w+(?:\s+\w+)*)\s*->\s*[a-zA-Z\s]+\s*->\s*(\w+(?:\s+\w+)*)"

        for node in nodes_retrieved:
            section_pattern = r"\n\n(.*?)\n\n"
            section_match = re.search(section_pattern, node.text, re.DOTALL)
            if section_match:
                relevant_section = section_match.group(1)
                print("Relevant Section:")
                print(relevant_section)

            else:
                print("No relevant section found.")

            for i in relevant_section.splitlines():
              print(f"rel: {i}")
              # Find all matches in the relevant section
              match = i.split(" -> ")


              print("Entity 1:", match[0])
              print("Entity 2:", match[2])

              entities.update(match[0])
              alist.append(match[0])
              entities.update(match[1])
              alist.append(match[1])
        print(f"Number of retrieved nodes {len(nodes_retrieved)}")
        for n in nodes_retrieved:
          print(n)

        # import ipdb;ipdb.set_trace()
        return list(set(alist))

    def retrieve_entity_communities(self, entity_info, entities):
        """
        Retrieve cluster information for given entities, allowing for multiple clusters per entity.

        Args:
        entity_info (dict): Dictionary mapping entities to their cluster IDs (list).
        entities (list): List of entity names to retrieve information for.

        Returns:
        List of community or cluster IDs to which an entity belongs.
        """
        community_ids = []

        for entity in entities:
            if entity in entity_info:
                community_ids.extend(entity_info[entity])

        return list(set(community_ids))


    def calculate_tokens(self, community_answers):
        from transformers import AutoTokenizer

        # Get the encoding for a specific model
        tokenizer = AutoTokenizer.from_pretrained("meta-llama/Meta-Llama-3-8B")  # For GPT-3.5-Turbo and GPT-4

        # Encode text into tokens
        text = FINAL_ANSWER_PROMPT + FINAL_ANSWER_CHAT_PROMPT
        encoding = tokenizer(text, return_tensors="pt")

        # Get tokenized IDs and check their length
        tokens = encoding["input_ids"][0]
        max_tokens = 8192-len(tokens)

        sum_tokens, final_value = 0, 0

        for content in community_answers:

          answer, _ = content
          tokens = encoding.encode(answer)
          sum_tokens += len(tokens)
          if sum_tokens >= max_tokens:
            break
          final_value += 1

        return final_value



    def generate_answer_from_summary(self, community_summary, query):
        """Generate an answer from a community summary based on a given query using LLM."""
        print("Community summary:", community_summary)
        prompt = (
            f"Given the community summary: {community_summary['summary']}, "
            f"how would you answer the following query? Query: {query}"
        )
        messages = [
            ChatMessage(role="system", content=prompt),
            ChatMessage(
                role="user",
                content="I need an answer based on the above information.",
            ),
        ]
        response = self.llm.chat(messages)
        cleaned_response = re.sub(r"^assistant:\s*", "", str(response)).strip()
        print(f"cleaned answer from summary: {cleaned_response}")

        if "I apologize" in cleaned_response or "there is no mention of" in cleaned_response:
          return None

        return (cleaned_response, community_summary['paper_ids'])

    def aggregate_answers(self, community_answers):
        """Aggregate individual community answers into a final, coherent response."""

        prompt = FINAL_ANSWER_PROMPT

        messages = [
            ChatMessage(role="system", content=FINAL_ANSWER_PROMPT),
            ChatMessage(
                role="user",
                content=f"{prompt}" + FINAL_ANSWER_CHAT_PROMPT            ),
        ]

        # print(community_answers)
        final_response = self.llm.chat(messages)
        cleaned_final_response = re.sub(
            r"^assistant:\s*", "", str(final_response)
        ).strip()

        return cleaned_final_response

##  Build End to End GraphRAG Pipeline

Now that we have defined all the necessary components, let’s construct the GraphRAG pipeline:

1. Create nodes/chunks from the text.
2. Build a PropertyGraphIndex using `GraphRAGExtractor` and `GraphRAGStore`.
3. Construct communities and generate a summary for each community using the graph built above.
4. Create a `GraphRAGQueryEngine` and begin querying.

### Create nodes/ chunks from the text.

In [ ]:
from llama_index.core.node_parser import SentenceSplitter

splitter = SentenceSplitter(
    chunk_size=1024,
    chunk_overlap=20,
)
nodes = splitter.get_nodes_from_documents(documents)

In [ ]:
len(nodes)

99

In [ ]:
nodes_df = pd.DataFrame(nodes)
nodes_df.to_csv('/content/output/extracted_nodes_99.csv')

In [ ]:
nodes_df.head()

0                  1   \
0  (id_, cfc199f6-484d-4efc-979a-6187fe4cf9b7)  (embedding, None)   
1  (id_, c0c64308-5875-4897-9009-6c709bf80611)  (embedding, None)   
2  (id_, 1720e05a-3194-40d9-aac7-8b6d72a2c04c)  (embedding, None)   
3  (id_, d2d8d8c5-7c01-4472-86e7-97dbddebb3c6)  (embedding, None)   
4  (id_, 60b32327-8d13-4abd-aeb7-384a926e43c3)  (embedding, None)   

                                       2                                   3   \
0  (metadata, {'paper_id': '2106.11517'})  (excluded_embed_metadata_keys, [])   
1  (metadata, {'paper_id': '2308.00479'})  (excluded_embed_metadata_keys, [])   
2  (metadata, {'paper_id': '2309.01105'})  (excluded_embed_metadata_keys, [])   
3  (metadata, {'paper_id': '2309.01431'})  (excluded_embed_metadata_keys, [])   
4  (metadata, {'paper_id': '2309.15217'})  (excluded_embed_metadata_keys, [])   

                                 4   \
0  (excluded_llm_metadata_keys, [])   
1  (excluded_llm_metadata_keys, [])   
2  (excluded_llm_metadata_keys, [])   
3  (excluded_llm_metadata_keys, [])   
4  (excluded_llm_metadata_keys, [])   

                                                  5   \
0  (relationships, {'NodeRelationship.SOURCE': no...   
1  (relationships, {'NodeRelationship.SOURCE': no...   
2  (relationships, {'NodeRelationship.SOURCE': no...   
3  (relationships, {'NodeRelationship.SOURCE': no...   
4  (relationships, {'NodeRelationship.SOURCE': no...   

                                    6                         7   \
0  (metadata_template, {key}: {value})  (metadata_separator, \n)   
1  (metadata_template, {key}: {value})  (metadata_separator, \n)   
2  (metadata_template, {key}: {value})  (metadata_separator, \n)   
3  (metadata_template, {key}: {value})  (metadata_separator, \n)   
4  (metadata_template, {key}: {value})  (metadata_separator, \n)   

                                                  8                       9   \
0  (text, ('Fine-tune the Entire RAG Architecture...  (mimetype, text/plain)   
1  (text, ('Retrieval Augmented Generation and Re...  (mimetype, text/plain)   
2  (text, ('A Study on the Implementation of Gene...  (mimetype, text/plain)   
3  (text, ('Benchmarking Large Language Models in...  (mimetype, text/plain)   
4  (text, ('RAGAS: Automated Evaluation of Retrie...  (mimetype, text/plain)   

                    10                    11                        12  \
0  (start_char_idx, 0)   (end_char_idx, 617)  (metadata_seperator, \n)   
1  (start_char_idx, 0)   (end_char_idx, 825)  (metadata_seperator, \n)   
2  (start_char_idx, 0)  (end_char_idx, 1884)  (metadata_seperator, \n)   
3  (start_char_idx, 0)  (end_char_idx, 1559)  (metadata_seperator, \n)   
4  (start_char_idx, 0)  (end_char_idx, 1201)  (metadata_seperator, \n)   

                                             13  
0  (text_template, {metadata_str}\n\n{content})  
1  (text_template, {metadata_str}\n\n{content})  
2  (text_template, {metadata_str}\n\n{content})  
3  (text_template, {metadata_str}\n\n{content})  
4  (text_template, {metadata_str}\n\n{content})

### Build ProperGraphIndex using `GraphRAGExtractor` and `GraphRAGStore`

In [ ]:
#####
## Knowledge triplet extraction prompt

KG_TRIPLET_EXTRACT_TMPL = """
-Goal-
Given a text document, identify all entities and their entity types from the text and all relationships among the identified entities.
Given the text, extract up to {max_knowledge_triplets} entity-relation triplets.

-Steps-
You must populate all the required fields and extract all the entities and entity pair relations from the whole text given to you.

1. Identify all entities. For each identified entity, extract the following information:
- entity_name: Name of the entity, capitalized
- entity_type: Type of the entity
- entity_description: Comprehensive description of the entity's attributes and activities


2. From the entities identified in step 1, identify all pairs of (source_entity, target_entity) that are related to each other. Get maximum relationships possible that make sense.
For each pair of related entities, extract the following information:
- source_entity: name of the source entity, as identified in step 1
- target_entity: name of the target entity, as identified in step 1
- relation: relationship between source_entity and target_entity
- relationship_description: explanation as to why you think the source entity and the target entity are related to each other

Extract as many entities and relationships possible from the text. Do not limit yourself by the format. The format is a guidance for how your text output must look.

Following is the text: {text}

It is crucial that you follow the following json format:
""" + \
"""
Format the entities as a json of the following structure (list of entitites) as
{"entities": [
    {
      "entity_name": "",
      "entity_type": "",
      "entity_description": ""
    },
    {
      "entity_name": "",
      "entity_type": "",
      "entity_description": ""
    },
    ...
    ]}
Similarly, format relationships as a json of the following structure (list of jsons) as
{"relationships": [
    {
      "source_name": "",
      "target_type": "",
      "relation"
      "relation_description": ""
    },
    {
      "source_name": "",
      "target_type": "",
      "relation"
      "relation_description": ""
    },
    ...
]}

Extract as many entities and relationships as possible from the text. Output ONLY the formatted entities and relationship each on a new line.
"""

In [ ]:
# parse llm response to store values in description
import json

def extract_json(text):
    pattern = r'```(.*?)```'
    bob = re.findall(pattern, text, re.DOTALL)
    if len(bob) == 2:
      return re.sub(r'\s+', ' ', bob[0].replace("\n", "")), re.sub(r'\s+', ' ', bob[1].replace("\n", ""))



def parse_fn(response_str: str):
    """
    Parses the JSON response to extract entities and relationships.

    Parameters:
        response_str (str): JSON response as a string.

    Returns:
        dict: A dictionary with 'entities' and 'relationships' keys containing lists of extracted data.
    """

    try:
      entities_json, relationships_json = extract_json(response_str)
      entities = json.loads(entities_json)
      relationships = json.loads(relationships_json)
    except Exception as e:
      print(e)
      return [], []


    # Parse entity triples
    entity_triples = []
    if entities_json and 'entities' in entities:
        for entity in entities['entities']:
            entity_triple = [
                entity['entity_name'],
                entity['entity_type'],
                entity['entity_description']
            ]
            entity_triples.append(entity_triple)

    # Parse relational triples
    relational_triples = []
    if relationships_json and 'relationships' in relationships:
        for relationship in relationships['relationships']:
            relational_triple = [
                relationship['source_name'] if 'source_name' in relationship.keys() else relationship['source_type'],
                relationship['relation'],
                relationship['target_name'] if 'target_name' in relationship.keys() else relationship['target_type'],
                relationship['relation_description']
            ]
            relational_triples.append(relational_triple)
    return entity_triples, relational_triples


# instantiate the Extractor class
kg_extractor = GraphRAGExtractor(
    llm=llm,
    extract_prompt=KG_TRIPLET_EXTRACT_TMPL,
    max_paths_per_chunk=2,
    parse_fn=parse_fn,
)

In [ ]:
print(nodes[5])

Node ID: fd3d7514-80f9-4309-8681-eae8803e668f
Text: ('Retrieval-Augmented Generation for Large Language Models: A
Survey', 'Yunfan Gao, Yun Xiong, Xinyu Gao, Kangxiang Jia, Jinliu Pan,
Yuxi Bi,\n  Yi Dai, Jiawei Sun, Meng Wang and Haofen Wang'):   Large
Language Models (LLMs) showcase impressive capabilities but encounter
challenges like hallucination, outdated knowledge, and non-
transparent, unt...


In [ ]:
import time

In [ ]:
main_index=None

In [ ]:
print(nodes )

[TextNode(id_='4254d8bf-02cf-4a03-9393-483b2d254e60', embedding=[0.002797260181978345, 0.002900532213971019, 0.03962801396846771, 0.006753886584192514, -0.01859792321920395, -0.015033268369734287, 0.014807489700615406, 0.013733177445828915, -0.0032107261940836906, -0.008851924911141396, 0.0461890883743763, -0.017231639474630356, -0.024989768862724304, -0.03723824396729469, -0.024448562413454056, -0.009438159875571728, 0.03460337221622467, -0.00639975443482399, 0.006354201585054398, -0.032347261905670166, 0.0298240277916193, -0.00978385005146265, 0.0005277578602544963, -0.02695568837225437, 0.026714960113167763, -0.00044712229282595217, 0.0030813447665423155, 0.021263349801301956, -0.03107590414583683, -0.03606145828962326, 0.013505389913916588, 0.00011527521564858034, 0.0017836961196735501, -0.05362465977668762, -0.008521807380020618, -0.018751487135887146, 0.0021931049413979053, -0.014318300411105156, -0.013941405341029167, 0.010983148589730263, 0.0009481036104261875, 0.00969928316771

In [ ]:
print(llm)

callback_manager=<llama_index.core.callbacks.base.CallbackManager object at 0x79cd4ff6ecb0> system_prompt=None messages_to_prompt=<function messages_to_prompt at 0x79ce5c248ca0> completion_to_prompt=<function default_completion_to_prompt at 0x79ce5c152170> output_parser=None pydantic_program_mode=<PydanticProgramMode.DEFAULT: 'default'> query_wrapper_prompt=None model='llama3-8b-8192' temperature=0.1 max_tokens=None logprobs=None top_logprobs=0 additional_kwargs={} max_retries=3 timeout=60.0 default_headers=None reuse_client=True api_key='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' api_base='https://api.groq.com/openai/v1' api_version='' strict=False context_window=3900 is_chat_model=True is_function_calling_model=True tokenizer=None


In [ ]:
index = PropertyGraphIndex(nodes=nodes,
    property_graph_store=GraphRAGStore(),
    kg_extractors=[kg_extractor],
    show_progress=True,
    llm = llm,
    embed_model=Settings.embed_model
)

Generating embeddings: 100%|██████████| 176/176 [09:48<00:00,  3.34s/it]  


In [ ]:
count_error

0

In [ ]:
print(index.property_graph_store.graph.nodes.values())

dict_values([ChunkNode(label='text_chunk', embedding=[0.002797260181978345, 0.002900532213971019, 0.03962801396846771, 0.006753886584192514, -0.01859792321920395, -0.015033268369734287, 0.014807489700615406, 0.013733177445828915, -0.0032107261940836906, -0.008851924911141396, 0.0461890883743763, -0.017231639474630356, -0.024989768862724304, -0.03723824396729469, -0.024448562413454056, -0.009438159875571728, 0.03460337221622467, -0.00639975443482399, 0.006354201585054398, -0.032347261905670166, 0.0298240277916193, -0.00978385005146265, 0.0005277578602544963, -0.02695568837225437, 0.026714960113167763, -0.00044712229282595217, 0.0030813447665423155, 0.021263349801301956, -0.03107590414583683, -0.03606145828962326, 0.013505389913916588, 0.00011527521564858034, 0.0017836961196735501, -0.05362465977668762, -0.008521807380020618, -0.018751487135887146, 0.0021931049413979053, -0.014318300411105156, -0.013941405341029167, 0.010983148589730263, 0.0009481036104261875, 0.009699283167719841, 0.029

In [ ]:
count_error

1

In [ ]:
list(index.property_graph_store.graph.nodes)[-2]

'Donggeon Han'

In [ ]:
list(index.property_graph_store.graph.nodes.values())

[ChunkNode(label='text_chunk', embedding=[0.002797260181978345, 0.002900532213971019, 0.03962801396846771, 0.006753886584192514, -0.01859792321920395, -0.015033268369734287, 0.014807489700615406, 0.013733177445828915, -0.0032107261940836906, -0.008851924911141396, 0.0461890883743763, -0.017231639474630356, -0.024989768862724304, -0.03723824396729469, -0.024448562413454056, -0.009438159875571728, 0.03460337221622467, -0.00639975443482399, 0.006354201585054398, -0.032347261905670166, 0.0298240277916193, -0.00978385005146265, 0.0005277578602544963, -0.02695568837225437, 0.026714960113167763, -0.00044712229282595217, 0.0030813447665423155, 0.021263349801301956, -0.03107590414583683, -0.03606145828962326, 0.013505389913916588, 0.00011527521564858034, 0.0017836961196735501, -0.05362465977668762, -0.008521807380020618, -0.018751487135887146, 0.0021931049413979053, -0.014318300411105156, -0.013941405341029167, 0.010983148589730263, 0.0009481036104261875, 0.009699283167719841, 0.029792925342917

In [ ]:
list(index.property_graph_store.graph.nodes.values())[-1].name

'Y. A. Illangasekara'

In [ ]:
list(index.property_graph_store.graph.nodes.values())[-2]

EntityNode(label='Author', embedding=None, properties={'paper_id': '2410.20878', 'entity_description': 'Author of the paper', 'triplet_source_id': 'a24a045d-279b-49cd-a982-9fc30b68a926'}, name='Donggeon Han')

In [ ]:
list(index.property_graph_store.graph.relations.values())[0].properties

{'paper_id': '2106.11517',
 'relationship_description': 'Shamane Siriwardhana is the author of the RAG Architecture',
 'triplet_source_id': '4254d8bf-02cf-4a03-9393-483b2d254e60'}

In [ ]:
list(index.property_graph_store.graph.relations.values())[0].properties

{'paper_id': '2106.11517',
 'relationship_description': 'The DPR Retriever is a component of the RAG Architecture',
 'triplet_source_id': '0e66e4b9-e749-4bd9-aa4a-6886ac2f2064'}

In [ ]:
data = []
for node in index.property_graph_store.graph.nodes.values():
    if hasattr(node, 'name'):
        row = {"name": node.name}
        row.update(node.properties)  # Add all properties as columns
        data.append(row)

# Create DataFrame
df = pd.DataFrame(data)

# Specify output folder and save as CSV
# output_folder = "output"
# os.makedirs(output_folder, exist_ok=True)  # Create the folder if it doesn't exist
csv_path =  "/content/output/entity_nodes.csv"
df.to_csv(csv_path, index=False)

print(f"Data saved to {csv_path}")

Data saved to /content/output/entity_nodes.csv


In [ ]:
df.head()

name    paper_id  \
0  Fine-tune the Entire RAG Architecture  2106.11517   
1                                    RAG  2410.20878   
2                          DPR retriever  2106.11517   
3                   Shamane Siriwardhana  2106.11517   
4                    Rivindu Weerasekera  2106.11517   

                      triplet_source_id  \
0  cfc199f6-484d-4efc-979a-6187fe4cf9b7   
1  f64ff187-9c1c-43bf-bb73-5cded7da4258   
2  cfc199f6-484d-4efc-979a-6187fe4cf9b7   
3  cfc199f6-484d-4efc-979a-6187fe4cf9b7   
4  cfc199f6-484d-4efc-979a-6187fe4cf9b7   

                            relationship_description entity_description  
0                                                NaN                NaN  
1       AutoRAG framework uses Large Language Models                NaN  
2  The RAG architecture is fine-tuned using the f...                NaN  
3  Shamane Siriwardhana and Elliott Wen co-author...                NaN  
4  The RAG architecture includes the DPR retrieve...                NaN

In [ ]:
data = []

for relation in index.property_graph_store.graph.relations.values():
    row = {
        "label": relation.label,
        "source_id": relation.source_id,
        "target_id": relation.target_id,
    }

    # Include all properties from the `properties` dictionary
    if hasattr(relation, "properties") and isinstance(relation.properties, dict):
        row.update(relation.properties)

    data.append(row)
print(data)
relation_df=pd.DataFrame(data)
csv_path =  "/content/output/relations.csv"
relation_df.to_csv(csv_path, index=False)

print(f"Relations saved to {csv_path}")

[{'label': 'is fine-tuned', 'source_id': 'Fine-tune the Entire RAG Architecture', 'target_id': 'RAG', 'paper_id': '2106.11517', 'relationship_description': 'The RAG architecture is fine-tuned using the fine-tune the Entire RAG Architecture method.', 'triplet_source_id': 'cfc199f6-484d-4efc-979a-6187fe4cf9b7'}, {'label': 'includes', 'source_id': 'RAG', 'target_id': 'DPR retriever', 'paper_id': '2106.11517', 'relationship_description': 'The RAG architecture includes the DPR retriever component.', 'triplet_source_id': 'cfc199f6-484d-4efc-979a-6187fe4cf9b7'}, {'label': 'co-authored', 'source_id': 'Shamane Siriwardhana', 'target_id': 'Rivindu Weerasekera', 'paper_id': '2106.11517', 'relationship_description': 'Shamane Siriwardhana and Rivindu Weerasekera co-authored the paper.', 'triplet_source_id': 'cfc199f6-484d-4efc-979a-6187fe4cf9b7'}, {'label': 'co-authored', 'source_id': 'Shamane Siriwardhana', 'target_id': 'Elliott Wen', 'paper_id': '2106.11517', 'relationship_description': 'Shamane 

In [ ]:
relation_df.head()

label                              source_id            target_id  \
0  is fine-tuned  Fine-tune the Entire RAG Architecture                  RAG   
1       includes                                    RAG        DPR retriever   
2    co-authored                   Shamane Siriwardhana  Rivindu Weerasekera   
3    co-authored                   Shamane Siriwardhana          Elliott Wen   
4    co-authored                   Shamane Siriwardhana  Suranga Nanayakkara   

     paper_id                           relationship_description  \
0  2106.11517  The RAG architecture is fine-tuned using the f...   
1  2106.11517  The RAG architecture includes the DPR retrieve...   
2  2106.11517  Shamane Siriwardhana and Rivindu Weerasekera c...   
3  2106.11517  Shamane Siriwardhana and Elliott Wen co-author...   
4  2106.11517  Shamane Siriwardhana and Suranga Nanayakkara c...   

                      triplet_source_id  
0  cfc199f6-484d-4efc-979a-6187fe4cf9b7  
1  cfc199f6-484d-4efc-979a-6187fe4cf9b7  
2  cfc199f6-484d-4efc-979a-6187fe4cf9b7  
3  cfc199f6-484d-4efc-979a-6187fe4cf9b7  
4  cfc199f6-484d-4efc-979a-6187fe4cf9b7

In [ ]:
df.shape

(785, 5)

In [ ]:
relation_df.shape

(408, 6)

In [ ]:
relation_df[relation_df['paper_id'].astype(str).str.startswith('2407.03955')]

label                                          source_id  \
240       refines  Meta-prompting Optimized Retrieval-augmented G...   
241  evaluated_on  Meta-prompting Optimized Retrieval-augmented G...   

                          target_id    paper_id  \
240  Retrieval-augmented Generation  2407.03955   
241              StrategyQA dataset  2407.03955   

                              relationship_description  \
240  Meta-prompting optimization refines the retrie...   
241  The method was evaluated on the StrategyQA dat...   

                        triplet_source_id  
240  fc94ec86-42a1-475b-b0f0-dc4b78ba1561  
241  fc94ec86-42a1-475b-b0f0-dc4b78ba1561

In [ ]:
df[df['paper_id'].astype(str).str.startswith('2407.03955')]

name    paper_id  \
42                      Retrieval-augmented Generation  2407.03955   
461  Meta-prompting Optimized Retrieval-augmented G...  2407.03955   
462                                 StrategyQA dataset  2407.03955   
463                                     João Rodrigues  2407.03955   
464                                     António Branco  2407.03955   

                        triplet_source_id  \
42   fc94ec86-42a1-475b-b0f0-dc4b78ba1561   
461  fc94ec86-42a1-475b-b0f0-dc4b78ba1561   
462  fc94ec86-42a1-475b-b0f0-dc4b78ba1561   
463  fc94ec86-42a1-475b-b0f0-dc4b78ba1561   
464  fc94ec86-42a1-475b-b0f0-dc4b78ba1561   

                              relationship_description  \
42                                                 NaN   
461  Meta-prompting optimization refines the retrie...   
462  Meta-prompting optimization refines the retrie...   
463                                                NaN   
464                                                NaN   

                  entity_description  
42                               NaN  
461                              NaN  
462                              NaN  
463  One of the authors of the paper  
464  One of the authors of the paper

### Build communities

This will create communities and summary for each community.

In [ ]:
# testing alternative community summary generation prompt
messages = [
            ChatMessage(
                role="system",
                content=(
                    # "You are provided with a set of relationships from a knowledge graph, each represented as "
                    # "entity1->entity2->paper_id->relation->relationship_description. Your task is to create a summary of these "
                    # "relationships. The summary should include the names of the entities involved and a concise synthesis "
                    # "of the relationship descriptions. The goal is to capture the most critical and relevant details that "
                    # "highlight the nature and significance of each relationship. Ensure that the summary is coherent and "
                    # "integrates the information in a way that emphasizes the key aspects of the relationships. "
                    # "End with the paper_ids from each knowledge graph by including them as a list in paranthesis."

                    "You are an expert knowledge graph analyst tasked with synthesizing complex entity relationships. "
                    "When generating the community summary, follow these comprehensive guidelines:\n\n"
                    "1. Relationship Analysis:\n"
                    "   - Identify and categorize the types of relationships between entities\n"
                    "   - Highlight the most significant and recurring relationship patterns\n"
                    "   - Capture the semantic meaning and context of each relationship\n\n"
                    "2. Comprehensive Synthesis:\n"
                    "   - Create a coherent narrative that explains the interconnections\n"
                    "   - Provide insights into how different entities are linked\n"
                    "   - Emphasize the broader implications of these relationships\n\n"
                    "3. Structural Approach:\n"
                    "   - Organize the summary with clear sections:\n"
                    "     a) Key Entities Overview\n"
                    "     b) Relationship Dynamics\n"
                    "     c) Significant Interconnections\n\n"
                    "4. Detailed Considerations:\n"
                    "   - Extract nuanced details from relationship descriptions\n"
                    "   - Identify potential themes or research directions\n"
                    "   - Maintain a balance between specificity and broader context\n\n"
                    "Formatting Requirements:\n"
                    "- Provide a concise yet comprehensive summary (200-400 words)\n"
                    "- Use clear, scholarly language\n"
                    "- End with a list of unique paper IDs in parentheses\n\n"
                    "Input Format: entity1 -> entity2 -> paper_id -> relation -> relationship_description. "
                    "If the community is mainly a connection of entities such as authors, which does not have much concrete context and information, feel free to write a short summary. "
                    "Otherwisee, be detailed in capturing the essence, specifics, and technical knowledge from the community."
                    "The summary must thoroughly reflect and capture specific and technical knowledge represented in the given text."
                ),
            ),
            ChatMessage(role="user", content="Recent advances in Retrieval-Augmented Generation (RAG) systems have popularized semantic chunking, which aims to improve retrieval performance by dividing documents into semantically coherent segments. Despite its growing adoption, the actual benefits over simpler fixed-size chunking, where documents are split into consecutive, fixed-size segments, remain unclear. This study systematically evaluates the effectiveness of semantic chunking using three common retrieval-related tasks: document retrieval, evidence retrieval, and retrieval-based answer generation. The results show that the computational costs associated with semantic chunking are not justified by consistent performance gains. These findings challenge the previous assumptions about semantic chunking and highlight the need for more efficient chunking strategies in RAG systems.	"),
        ]
response = llm.chat(messages)


In [ ]:
print(response)

assistant: **Key Entities Overview**

The study focuses on Retrieval-Augmented Generation (RAG) systems, specifically semantic chunking, a technique aimed at improving retrieval performance by dividing documents into semantically coherent segments.

**Relationship Dynamics**

The study evaluates the effectiveness of semantic chunking using three common retrieval-related tasks: document retrieval, evidence retrieval, and retrieval-based answer generation. The results show that the computational costs associated with semantic chunking do not yield consistent performance gains, challenging previous assumptions about its benefits.

**Significant Interconnections**

The study highlights the need for more efficient chunking strategies in RAG systems, suggesting that simpler fixed-size chunking may be sufficient. The findings also underscore the importance of systematic evaluations in understanding the actual benefits of semantic chunking.

**Detailed Considerations**

The study's results hav

In [ ]:
llm = Groq(model="llama3-8b-8192", api_key=api_key_latest)

In [ ]:
Settings.llm = llm

In [ ]:
index.property_graph_store.build_communities()


 LLM currently used:  callback_manager=<llama_index.core.callbacks.base.CallbackManager object at 0x79380b8eb970> system_prompt=None messages_to_prompt=<function messages_to_prompt at 0x7938fb7b8af0> completion_to_prompt=<function default_completion_to_prompt at 0x7938fb6a09d0> output_parser=None pydantic_program_mode=<PydanticProgramMode.DEFAULT: 'default'> query_wrapper_prompt=None model='llama3-8b-8192' temperature=0.1 max_tokens=None logprobs=None top_logprobs=0 additional_kwargs={} max_retries=3 timeout=60.0 default_headers=None reuse_client=True api_key='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' api_base='https://api.groq.com/openai/v1' api_version='' strict=False context_window=3900 is_chat_model=True is_function_calling_model=True tokenizer=None
CLUSTERS:  
 [HierarchicalCluster(node='LLMs', cluster=0, parent_cluster=None, level=0, is_final_cluster=False), HierarchicalCluster(node='RAGEval', cluster=0, parent_cluster=None, level=0, is_final_cluster=False), Hier

/usr/local/lib/python3.10/dist-packages/graspologic/partition/leiden.py:607: UserWarning: Leiden partitions do not contain all nodes from the input graph because input graph contained isolate nodes.
  warnings.warn(


details: Shamane Siriwardhana -> Rivindu Weerasekera -> 2106.11517-> co-authored -> Shamane Siriwardhana and Rivindu Weerasekera co-authored the paper.
Shamane Siriwardhana -> Elliott Wen -> 2106.11517-> co-authored -> Shamane Siriwardhana and Elliott Wen co-authored the paper.
Shamane Siriwardhana -> Suranga Nanayakkara -> 2106.11517-> co-authored -> Shamane Siriwardhana and Suranga Nanayakkara co-authored the paper.
Rivindu Weerasekera -> Shamane Siriwardhana -> 2106.11517-> co-authored -> Shamane Siriwardhana and Rivindu Weerasekera co-authored the paper.
Elliott Wen -> Shamane Siriwardhana -> 2106.11517-> co-authored -> Shamane Siriwardhana and Elliott Wen co-authored the paper.
Suranga Nanayakkara -> Shamane Siriwardhana -> 2106.11517-> co-authored -> Shamane Siriwardhana and Suranga Nanayakkara co-authored the paper..
details: OpenAI -> The Chronicles of RAG -> 2401.07883-> Model Developer -> OpenAI developed the gpt-4, gpt-4-1106-preview, and gpt-3.5-turbo-1106 models used in th

## Saving build

In [ ]:
# from llama_index.core.storage_context import StorageContext
from llama_index.core import StorageContext
storage_context = StorageContext.from_defaults(
    # property_graph_store=GraphRAGStore(),
    graph_store= GraphRAGStore()
)

In [ ]:
persist_dir = "/content/output/index_data_graphrag"
index.storage_context.persist(persist_dir=persist_dir)

In [ ]:
print(index.property_graph_store.community_mapping)

{'LLMs': 54, 'RAGEval': 54, 'AutoRAG': 57, 'RAGAS': 53, 'Shahul Es': 53, 'Jithin James': 53, 'Luis Espinosa-Anke': 53, 'Steven Schockaert': 53, 'R^2AG': 56, 'Retrievers': 56, 'Retrieval-augmented Generation': 56, 'RAU': 54, 'Documents': 55, 'DPrompt tuning': 54, 'Meta-prompting Optimized Retrieval-augmented Generation': 56, 'Enterprise retrieval augmented generation (RAG)': 55, 'Enterprise LLM': 55, 'GitHub': 57, 'SAM-RAG': 57, 'StrategyQA dataset': 56, 'Kunlun Zhu': 54, 'Multimodal Retrieval-Augmented Generation': 57, 'Dongkyu Kim, Byoungwook Kim, Donggeon Han and Matouš Eibich': 57, 'Shamane Siriwardhana': 1, 'Rivindu Weerasekera': 1, 'Elliott Wen': 1, 'Suranga Nanayakkara': 1, 'OpenAI': 2, 'The Chronicles of RAG': 2, 'Paulo Finardi': 2, 'Leonardo Avila': 2, 'Rodrigo Castaldoni': 2, 'Pedro Gengo': 2, 'Celio Larcher': 2, 'Marcos Piau': 2, 'Pablo Costa': 2, "Vinicius Carid'a": 2, 'Google': 2, 'Harry Potter': 2, 'Retrieval-Augmented Generation (RAG)': 58, 'RAGCache': 65, 'FlashRAG': 59,

In [ ]:
data = []
# save entities
for node in index.property_graph_store.graph.nodes.values():
    if hasattr(node, 'name'):
        row = {"name": node.name}
        row.update(node.properties)  # Add all properties as columns
        data.append(row)

# Create DataFrame
df = pd.DataFrame(data)

# Specify output folder and save as CSV
# output_folder = "output"
# os.makedirs(output_folder, exist_ok=True)  # Create the folder if it doesn't exist
csv_path =  "/content/output/entity_nodes.csv"
df.to_csv(csv_path, index=False)

print(f"Data saved to {csv_path}")

In [ ]:
data = []
# save relations
for relation in index_loaded.property_graph_store.graph.relations.values():
    row = {
        "label": relation.label,
        "source_id": relation.source_id,
        "target_id": relation.target_id,
    }

    # Include all properties from the `properties` dictionary
    if hasattr(relation, "properties") and isinstance(relation.properties, dict):
        row.update(relation.properties)

    data.append(row)
print(data)
relation_df=pd.DataFrame(data)
csv_path =  "/content/output/relations.csv"
relation_df.to_csv(csv_path, index=False)

print(f"Relations saved to {csv_path}")

[{'label': 'Component', 'source_id': 'RAG Architecture', 'target_id': 'DPR Retriever', 'paper_id': '2106.11517', 'relationship_description': 'The DPR Retriever is a component of the RAG Architecture', 'triplet_source_id': '0e66e4b9-e749-4bd9-aa4a-6886ac2f2064'}, {'label': 'Co-author', 'source_id': 'Shamane Siriwardhana', 'target_id': 'Rivindu Weerasekera', 'paper_id': '2106.11517', 'relationship_description': 'Shamane Siriwardhana and Rivindu Weerasekera are co-authors of the paper', 'triplet_source_id': '0e66e4b9-e749-4bd9-aa4a-6886ac2f2064'}, {'label': 'uses', 'source_id': 'Large Language Models', 'target_id': 'Retrieval Augmented Generation', 'paper_id': '2308.00479', 'relationship_description': 'Large Language Models use Retrieval Augmented Generation to produce high-quality text', 'triplet_source_id': 'ca47c282-e329-4e81-984c-1892205a3c18'}, {'label': 'applies_to', 'source_id': 'Retrieval Augmented Generation', 'target_id': 'Medical Education', 'paper_id': '2308.00479', 'relations

In [ ]:
import shutil

# Define the directory to be zipped and the output zip file
output_dir = "/content/output"  # Replace with your output directory path
zip_file = "/content/output.zip"  # Replace with your desired zip file path

# Create a zip file from the directory
shutil.make_archive(zip_file.replace('.zip', ''), 'zip', output_dir)

print(f"Directory {output_dir} has been zipped into {zip_file}")

Directory /content/output has been zipped into /content/output.zip


## Visualization

In [ ]:
 def visualize_community_graph(nx_graph, community_mapping):
      """Visualize the graph with community-based coloring and detailed node information."""
      from pyvis.network import Network

      # Create a NetworkX graph from the stored graph representation
      nx_graph = nx_graph
      # print("\n\n CLUSTERS: ", self.clusters)
      # Initialize PyVis network
      net = Network(notebook=False, height="750px", width="100%", directed=False)

      # Map each node to its community
      community_mapping = community_mapping
      # print("\n\n COMMUNITY MAPPING", community_mapping)

      # Generate colors for each community
      import matplotlib.pyplot as plt
      num_communities = len(set(community_mapping.values()))
      color_map = plt.cm.get_cmap("hsv", num_communities)
      community_colors = {}
      color_threshold = 0.25  # Adjust this to control how "different" RGB values must be
      # num_communities = len(color_map.colors)

      for cluster_id, (r, g, b, _) in zip(range(num_communities), color_map(np.linspace(0, 1, num_communities))):
          # Avoid shades of grey by ensuring RGB values are not too close
          if abs(r - g) < color_threshold and abs(g - b) < color_threshold and abs(b - r) < color_threshold:
              # If it's grey-like, skip or adjust to a random vibrant color
              continue

          community_colors[cluster_id] = f"#{int(255 * r):02x}{int(255 * g):02x}{int(255 * b):02x}"

      # Add nodes with community colors and metadata
      for node, data in nx_graph.nodes(data=True):
          node_name= node.split("({")[0]
          print(f"\n\n Printing from Viz\n Node: {node_name}, Data: {data}")
          community_id = community_mapping.get(node, -1)
          color = community_colors.get(community_id, "##28282B")  # Default to black if no community
          title = f"Node: {node_name}\n"
          # import ipdb; ipdb.set_trace()
          title += f"Paper ID: { data.get('paper_id', 'N/A')}\n"
          title += f"Community:{community_id}"
          # title += f"<b>Descriptions:</b> {', '.join(data.get('descriptions', []))}<br>"
          print("Final Title\n", title)
          net.add_node(
              node,
              label=node_name,
              title=title,
              color=color
          )

      # Add edges with metadata
      for u, v, data in nx_graph.edges(data=True):
          # import ipdb; ipdb.set_trace()
          # print("\n Edge info ",str(u)+str(v)+str(data))
          title = f"Relationship: {data.get('relationship', 'N/A')}\n"
          title += f"Description: {data.get('description', 'N/A')}\n"
          title += f"Paper ID: {data.get('paper_id', 'N/A')}"
          print("\nEdge title ", title)
          net.add_edge(
              u,
              v,
              title=title
          )


      # import ipdb; ipdb.set_trace()
      # print(net)
      # Show the graph
      # net.show("community_graph.html")
      net.save_graph("graph_visualization_1.html")
      print("Community graph visualization saved as 'graph_visualization.html'")

In [ ]:
import numpy as np
visualize_community_graph(index.property_graph_store.nx_graph, index.property_graph_store.community_mapping)

<ipython-input-54-b48170768776>:18: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed two minor releases later. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap(obj)`` instead.
  color_map = plt.cm.get_cmap("hsv", num_communities)


Streaming output truncated to the last 5000 lines.

 Printing from Viz
 Node: Linhao Zhang , Data: {'paper_id': '2410.12248'}
Final Title
 Node: Linhao Zhang 
Paper ID: 2410.12248
Community:-1


 Printing from Viz
 Node: Pengjun Xie , Data: {'paper_id': '2410.12248'}
Final Title
 Node: Pengjun Xie 
Paper ID: 2410.12248
Community:-1


 Printing from Viz
 Node: Fie Huang , Data: {'paper_id': '2410.12248'}
Final Title
 Node: Fie Huang 
Paper ID: 2410.12248
Community:-1


 Printing from Viz
 Node: Shailja Gupta , Data: {'paper_id': '2410.12837'}
Final Title
 Node: Shailja Gupta 
Paper ID: 2410.12837
Community:-1


 Printing from Viz
 Node: Rajesh Ranjan , Data: {'paper_id': '2410.12837'}
Final Title
 Node: Rajesh Ranjan 
Paper ID: 2410.12837
Community:-1


 Printing from Viz
 Node: Surya Narayan Singh , Data: {'paper_id': '2410.12837'}
Final Title
 Node: Surya Narayan Singh 
Paper ID: 2410.12837
Community:-1


 Printing from Viz
 Node: Knowledge Retrieval , Data: {'paper_id': '2410.13258'}

In [ ]:
print(index.property_graph_store.cluster)

[HierarchicalCluster(node='RAG Architecture', cluster=0, parent_cluster=None, level=0, is_final_cluster=True), HierarchicalCluster(node='DPR Retriever', cluster=0, parent_cluster=None, level=0, is_final_cluster=True), HierarchicalCluster(node='HuggingFace Transformers Library', cluster=0, parent_cluster=None, level=0, is_final_cluster=True), HierarchicalCluster(node='Shamane Siriwardhana', cluster=1, parent_cluster=None, level=0, is_final_cluster=True), HierarchicalCluster(node='Rivindu Weerasekera', cluster=1, parent_cluster=None, level=0, is_final_cluster=True), HierarchicalCluster(node='Large Language Models', cluster=2, parent_cluster=None, level=0, is_final_cluster=False), HierarchicalCluster(node='Retrieval Augmented Generation', cluster=2, parent_cluster=None, level=0, is_final_cluster=False), HierarchicalCluster(node='Retrieval-augmented Generation', cluster=2, parent_cluster=None, level=0, is_final_cluster=False), HierarchicalCluster(node='RQ-RAG', cluster=2, parent_cluster=No

In [ ]:
list(index_loaded.property_graph_store.graph.relations.values())

[Relation(label='Modification', source_id='Fine-tune the Entire RAG Architecture', target_id='RAG Architecture', properties={'paper_id': '2106.11517', 'relationship_description': 'The fine-tuning technique is applied to the RAG architecture.', 'triplet_source_id': '22918700-0a1a-4852-92ff-475107fdf6af'}),
 Relation(label='Component', source_id='RAG Architecture', target_id='DPR Retriever', properties={'paper_id': '2106.11517', 'relationship_description': 'The DPR retriever is a component of the RAG architecture.', 'triplet_source_id': '22918700-0a1a-4852-92ff-475107fdf6af'}),
 Relation(label='Development', source_id='Shamane Siriwardhana', target_id='RAG Architecture', properties={'paper_id': '2106.11517', 'relationship_description': 'Shamane Siriwardhana was involved in the development of the RAG architecture.', 'triplet_source_id': '22918700-0a1a-4852-92ff-475107fdf6af'}),
 Relation(label='uses', source_id='Large Language Models', target_id='Retrieval Augmented Generation', propertie

In [ ]:
# so is the above also taking the relational triplet as a node?

In [ ]:
index.property_graph_store

# Create QueryEngine

Retrieval and Response Generation

In [ ]:
# instantiating the query engine
query_engine = GraphRAGQueryEngine(
    graph_store=index.property_graph_store,
    index=index,
    llm=llm,
    similarity_top_k=10,
)


In [ ]:
response = query_engine.query(
    "What techniques can improve factual accuracy in large language models for open-domain question answering? Discuss retrieval-augmented generation (RAG), fine-tuning with knowledge bases, and evaluation metrics to measure accuracy."
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large Language Model (LLM)
rel: Large Language Model (LLM) -> Model used -> ARAGOG
Entity 1: Large Language Model (LLM)
Entity 2: ARAGOG
rel: Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
Entity 1: Large Language Model (LLM)
Entity 2: Retrieval Augmented Generation
rel: P-RAG -> related_to -> Embodied Everyday Task
Entity 1: P-RAG
Entity 2: Embodied Everyday Task
Relevant Section:
Corrective Retrieval Augmented Generation -> Extends -> Retrieval-Augmented Generation
Corrective Retrieval Augmented Generation -> Improves -> Large Language Models
rel: Corrective Retrieval Augmented Generation -> Extends -> Retrieval-Augmented Generation
Entity 1: Corr

Response:

The techniques that can improve factual accuracy in large language models for open-domain question answering are Retrieval-Augmented Generation (RAG), fine-tuning with knowledge bases, and evaluation metrics. RAG enhances large language models by sourcing relevant text chunks from external knowledge bases, which can improve factual accuracy by incorporating external knowledge and authoritative sources (2406.11201). Fine-tuning with knowledge bases involves training the models on large datasets of factual information, such as knowledge graphs or databases, to improve their ability to generate accurate and informative responses (2403.05676).

Evaluation metrics are crucial in measuring the accuracy of large language models. Beneficial noise, which can enhance the performance of LLMs, can be used to evaluate their ability to generate accurate responses. Harmful noise, on the other hand, can be used to assess their robustness to errors (2405.12363). Other metrics, such as precision, recall, and F1-score, can be used to evaluate the accuracy of LLMs in open-domain question answering tasks.

Some specific techniques that can improve factual accuracy in LLMs include M-RAG, FS-RAG, and Graph Retrieval-Augmented Generation (2405.1642, 2406.16167, 2408.08921). These techniques can be used in combination to improve the factual accuracy of LLMs for open-domain question answering.

In addition to these techniques, other methods such as query-dependent retrievals, multimodal retrieval techniques, and knowledge selection can also be used to improve the factual accuracy of LLMs for open-domain question answering (2407.16833, 2407.16833, 2407.16833). Overall, a combination of techniques such as RAG, fine-tuning with knowledge bases, and evaluation metrics can help improve the factual accuracy of LLMs for open-domain question answering.

References:

* 2406.11201: OpenAI highlights the process of fine-tuning LLMs
* 2403.05676: Fine-Tuning Large Language Models with Knowledge Graphs for Open-Domain Question Answering
* 2405.12363: Evaluation Metrics for Open-Domain Question Answering: A Survey
* 2405.1642: M-RAG: A Technique for Improving Factual Accuracy in LLMs
* 2406.16167: FS-RAG: A Technique for Improving Factual Accuracy in LLMs
* 2408.08921: Graph Retrieval-Augmented Generation: A Technique for Improving Factual Accuracy in LLMs
* 2407.16833: Query-Dependent Retrievals: A Technique for Improving Factual Accuracy in LLMs
* 2407.16833: Multimodal Retrieval Techniques: A Technique for Improving Factual Accuracy in LLMs
* 2407.16833: Knowledge Selection: A Technique for Improving Factual Accuracy in LLMs

In [ ]:
response = query_engine.query(
    "How does Retrieval-Augmented Generation (RAG) address the limitations of Large Language Models (LLMs), particularly in terms of hallucinations and knowledge consistency?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large Language Model (LLM)
rel: Large Language Model (LLM) -> Model used -> ARAGOG
Entity 1: Large Language Model (LLM)
Entity 2: ARAGOG
rel: Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
Entity 1: Large Language Model (LLM)
Entity 2: Retrieval Augmented Generation
rel: P-RAG -> related_to -> Embodied Everyday Task
Entity 1: P-RAG
Entity 2: Embodied Everyday Task
Relevant Section:
Neeltje Kackar -> Author -> RAGS4EIC
Cristiano Fanelli -> Author -> RAGS4EIC
Luke Schleck -> Author -> RAGS4EIC
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
Entity 2: RAGS4EIC
rel: Cristiano Fanel

Response:

Retrieval-Augmented Generation (RAG) is a method that leverages Large Language Models (LLMs) to generate responses by incorporating retrieved contexts. While RAG has been shown to improve the quality of structured output and enhance question-answering capabilities (2409.15699), its ability to address the limitations of LLMs, particularly in terms of hallucinations and knowledge consistency, remains unclear.

One paper suggests that RAG may address hallucinations by incorporating retrieved contexts, which can provide a more accurate and reliable source of information (2409.15699). This approach can help reduce the likelihood of generating responses that are not grounded in reality. However, the paper does not provide specific information on how RAG addresses hallucinations.

Regarding knowledge consistency, RAG's ability to retrieve and integrate domain-specific information from external sources may help improve knowledge consistency by providing a more comprehensive and accurate understanding of the topic (2404.08189). The paper "Knowledge Retrieval" discusses the use of RAG to retrieve relevant knowledge from external sources, and the paper "Knowledge Selection" discusses the use of RAG to select the most relevant knowledge from the retrieved knowledge, which may help ensure knowledge consistency (2404.10981).

In conclusion, while RAG has been shown to improve the quality of structured output and enhance question-answering capabilities, its ability to address the limitations of LLMs, particularly in terms of hallucinations and knowledge consistency, remains unclear. Further research is needed to fully understand how RAG addresses these limitations.

References:

* 2409.15699. "Retrieval-Augmented Generation: A Method for Improving the Quality of Structured Output and Enhancing Question-Answering Capabilities."
* 2404.08189. "Knowledge Retrieval: A Method for Retrieving Relevant Knowledge from External Sources."
* 2404.10981. "Knowledge Selection: A Method for Selecting the Most Relevant Knowledge from Retrieved Knowledge."

In [ ]:
response = query_engine.query(
    "What are the key challenges in implementing effective RAG systems, and what innovative approaches have researchers proposed to overcome these challenges?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
Neeltje Kackar -> Author -> RAGS4EIC
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Luke Schleck -> Author -> RAGS4EIC
Cristiano Fanelli -> Author -> RAGS4EIC
Karthik Suresh -> Author -> RAGS4EIC
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
Entity 2: RAGS4EIC
rel: RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Entity 1: RAGS4EIC
Entity 2: Electron-Ion Collider (EIC)
rel: Luke Schleck -> Author -> RAGS4EIC
Entity 1: Luke Schleck
Entity 2: RAGS4EIC
rel: Cristiano Fanelli -> Author -> RAGS4EIC
Entity 1: Cristiano Fanelli
Entity 2: RAGS4EIC
rel: Karthik Suresh -> Author -> RAGS4EIC
Entity 1: Karthik Suresh
Entity 2: RAGS4EIC
Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large

Response:

he implementation of effective Retrieval-Augmented Generation (RAG) systems is a complex task that requires addressing various challenges. While the provided context does not explicitly mention the key challenges, it is possible to infer some potential challenges and innovative approaches proposed by researchers to overcome them.

One challenge that can be inferred is the need to improve the robustness of RAG systems. Corrective Retrieval Augmented Generation, for example, aims to improve the robustness of Large Language Models (LLMs) by incorporating a lightweight retrieval evaluator and a decompose-then-recompose algorithm (2404.01037). This suggests that one challenge is ensuring the robustness of RAG systems, and researchers have proposed using these techniques to address this issue.

Another challenge that can be inferred is the need to enhance the factual accuracy of RAG-generated text. FS-RAG, for instance, aims to improve the factual accuracy of LLMs (2404.07221). This implies that another challenge is ensuring the accuracy of RAG-generated text, and researchers have proposed using this approach to address this issue.

In addition, the integration of external knowledge into RAG systems is another challenge that can be inferred. RA-LLMs and M-RAG, for example, enhance LLMs by retrieving relevant memories from an external database (2401.15884, 2405.06211). This suggests that one challenge is integrating external knowledge into RAG systems, and researchers have proposed using these approaches to address this issue.

Furthermore, evaluating and enhancing the capabilities of RAG systems is another challenge that can be inferred. CoFE-RAG, for instance, evaluates and enhances the capabilities of LLMs (2405.1642). This implies that another challenge is evaluating and improving the performance of RAG systems, and researchers have proposed using this approach to address this issue.

Innovative approaches proposed by researchers to overcome these challenges include using retrieval-augmented generation techniques, integrating external knowledge sources, developing evaluation metrics and approaches, and fine-tuning LLMs using OpenAI's process and integrating them within RAG pipelines. These approaches aim to improve the robustness, factual accuracy, and overall performance of RAG systems, making them more effective and reliable.

In conclusion, while the provided context does not explicitly mention the key challenges in implementing effective RAG systems, it is possible to infer some potential challenges and innovative approaches proposed by researchers to overcome them. These challenges and approaches highlight the complexity of RAG systems and the need for continued research and innovation to improve their effectiveness.

References:

* 2404.01037: ARAGOG: Hypothetical Document Embedding for Retrieval-Augmented Generation
* 2404.07221: FS-RAG: Factual Accuracy RAG
* 2401.15884: RA-LLMs: Retrieval-Augmented Large Language Models
* 2405.06211: M-RAG: Memory-Augmented RAG
* 2405.1642: CoFE-RAG: Contextualized Fusion and Evaluation RAG

In [ ]:
response = query_engine.query(
    "How can RAG techniques be optimized to improve reasoning capabilities and knowledge retrieval in complex, knowledge-intensive tasks?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large Language Model (LLM)
rel: Large Language Model (LLM) -> Model used -> ARAGOG
Entity 1: Large Language Model (LLM)
Entity 2: ARAGOG
rel: Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
Entity 1: Large Language Model (LLM)
Entity 2: Retrieval Augmented Generation
rel: P-RAG -> related_to -> Embodied Everyday Task
Entity 1: P-RAG
Entity 2: Embodied Everyday Task
Relevant Section:
Large Language Models -> Augmented -> Retrieval-Augmented Large Language Models
rel: Large Language Models -> Augmented -> Retrieval-Augmented Large Language Models
Entity 1: Large Language Models
Entity 2: Retrieval-Augmented Large Language Models
Relevant Section:
Yunfa

Response:
Optimizing Retrieval-Augmented Generation (RAG) techniques is crucial for improving reasoning capabilities and knowledge retrieval in complex, knowledge-intensive tasks. To achieve this, several strategies can be employed. Firstly, leveraging Multi-Agent Reinforcement Learning (M-RAG) can optimize different language generation tasks explicitly, enhancing the reasoning capabilities of RAG (2404.07221). Secondly, incorporating large-scale web searches and a decompose-then-recompose algorithm, as in FS-RAG, can improve the factual accuracy of Large Language Models (LLMs) and enhance knowledge retrieval (2401.15884). Additionally, referencing an external knowledge base to refine LLM outputs, as in Graph Retrieval-Augmented Generation, can provide more accurate and relevant information, improving reasoning capabilities and knowledge retrieval (2406.11201).

Another approach is to use CoFE-RAG, which evaluates and enhances the capabilities of LLMs by contextualizing the fusion of retrieved information (2405.06211). Furthermore, M-RAG can be used to enhance LLMs by retrieving relevant memories from an external database, providing more accurate and relevant information (2405.1642). FunnelRAG can also be employed as a paradigm for RAG, improving the efficiency and effectiveness of knowledge retrieval and reasoning (2404.07221).

Modular RAG is another transformative technology that converts RAG systems into reconfigurable frameworks, enabling them to be more modular and adaptable (2407.21059). This transformation enhances the capabilities of LLMs in tackling knowledge-intensive tasks. Moreover, Continuous knowledge updates, query-dependent retrievals, multimodal retrieval techniques, knowledge selection, and combination with other techniques can be employed to optimize RAG techniques (2409.15699).

In conclusion, optimizing RAG techniques for improving reasoning capabilities and knowledge retrieval in complex, knowledge-intensive tasks requires the consideration of various strategies. These strategies include leveraging M-RAG, FS-RAG, Graph Retrieval-Augmented Generation, CoFE-RAG, M-RAG, FunnelRAG, Modular RAG, and continuous knowledge updates, query-dependent retrievals, multimodal retrieval techniques, knowledge selection, and combination with other techniques.

References:

2404.07221. Leverage Multi-Agent Reinforcement Learning to optimize different language generation tasks explicitly, enhancing the reasoning capabilities of RAG.

2401.15884. Incorporate large-scale web searches and a decompose-then-recompose algorithm to improve the factual accuracy of LLMs and enhance knowledge retrieval.

2406.11201. Reference an external knowledge base to refine LLM outputs, providing more accurate and relevant information, improving reasoning capabilities and knowledge retrieval.

2405.06211. Use CoFE-RAG to evaluate and enhance the capabilities of LLMs by contextualizing the fusion of retrieved information.

2405.1642. Use M-RAG to enhance LLMs by retrieving relevant memories from an external database, providing more accurate and relevant information.

2404.07221. Employ FunnelRAG as a paradigm for RAG, improving the efficiency and effectiveness of knowledge retrieval and reasoning.

2407.21059. Use Modular RAG to convert RAG systems into reconfigurable frameworks, enabling them to be more modular and adaptable.

2409.15699. Employ continuous knowledge updates, query-dependent retrievals, multimodal retrieval techniques, knowledge selection, and combination with other techniques to optimize RAG techniques.


In [ ]:
response = query_engine.query(
    "What are the most promising methods for enhancing the efficiency and performance of RAG systems, particularly in terms of computational overhead and context compression?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
Neeltje Kackar -> Author -> RAGS4EIC
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Cristiano Fanelli -> Author -> RAGS4EIC
Luke Schleck -> Author -> RAGS4EIC
Karthik Suresh -> Author -> RAGS4EIC
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
Entity 2: RAGS4EIC
rel: RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Entity 1: RAGS4EIC
Entity 2: Electron-Ion Collider (EIC)
rel: Cristiano Fanelli -> Author -> RAGS4EIC
Entity 1: Cristiano Fanelli
Entity 2: RAGS4EIC
rel: Luke Schleck -> Author -> RAGS4EIC
Entity 1: Luke Schleck
Entity 2: RAGS4EIC
rel: Karthik Suresh -> Author -> RAGS4EIC
Entity 1: Karthik Suresh
Entity 2: RAGS4EIC
Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large

Response:
The optimization of Retrieval-Augmented Generation (RAG) systems has been a topic of significant interest in recent years, particularly in terms of computational overhead and context compression. Several methods have been proposed to enhance the efficiency and performance of RAG systems, including RAGCache, Scalable and Pluggable Virtual Tokens, R^2AG, Hybrid RAG System, and StructRAG (Kumar et al., 2021; Li et al., 2022; Suresh et al., 2022).

One promising approach is the use of query-dependent retrievals, which can help reduce computational overhead by retrieving only the most relevant knowledge from external sources (Kumar et al., 2021). Multimodal retrieval techniques can also improve the performance of RAG systems by retrieving knowledge from multiple sources and modalities (Li et al., 2022). Additionally, knowledge selection techniques can be used to select the most relevant knowledge from the retrieved knowledge, further improving the performance of RAG systems (Suresh et al., 2022).

Another approach is the use of fine-tuning the Large Language Model (LLM) for retrieval augmented generation, as demonstrated in the ARAGOG research paper (2404.01037). This method can effectively compress context and reduce computational overhead. The Hypothetical Document Embedding (HyDE) method, used in ARAGOG, can also be employed to efficiently retrieve relevant information from the database (2404.01037). Furthermore, the Sentence Window Retrieval method, also used in ARAGOG, can be utilized to efficiently retrieve relevant information from the database (2404.01037).

In addition, leveraging the powerful language processing capabilities of LLMs, as shown in the P-RAG research paper (2409.11279), can improve the performance of RAG systems. Modular RAG, which converts RAG systems into reconfigurable frameworks, similar to LEGO blocks, can also be used to enhance the efficiency and performance of RAG systems (2407.21059).

In conclusion, several methods have been proposed to enhance the efficiency and performance of RAG systems, including query-dependent retrievals, multimodal retrieval techniques, knowledge selection, fine-tuning the LLM, HyDE, Sentence Window Retrieval, and Modular RAG. These methods can help reduce computational overhead and improve context compression, making RAG systems more efficient and effective.

References:

Kumar, et al. (2021). RAGCache: A caching-based approach for efficient retrieval-augmented generation. arXiv preprint arXiv:2104.01037.

Li, et al. (2022). Scalable and pluggable virtual tokens for retrieval-augmented generation. arXiv preprint arXiv:2203.05676.

Suresh, et al. (2022). Towards a RAG-based Summarization Agent for the Electron-Ion Collider. arXiv preprint arXiv:2203.15729.

ARAGOG (2022). ARAGOG: A retrieval-augmented generation framework. arXiv preprint arXiv:2204.01037.

P-RAG (2022). P-RAG: A powerful language processing framework for retrieval-augmented generation. arXiv preprint arXiv:2209.11279.

Modular RAG (2022). Modular RAG: A reconfigurable framework for retrieval-augmented generation. arXiv preprint arXiv:2207.21059.

In [ ]:
response = query_engine.query(
    "How do different RAG approaches handle the selection and preprocessing of external knowledge sources to improve generation quality?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
Cristiano Fanelli -> Author -> RAGS4EIC
Neeltje Kackar -> Author -> RAGS4EIC
Luke Schleck -> Author -> RAGS4EIC
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
rel: Cristiano Fanelli -> Author -> RAGS4EIC
Entity 1: Cristiano Fanelli
Entity 2: RAGS4EIC
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
Entity 2: RAGS4EIC
rel: Luke Schleck -> Author -> RAGS4EIC
Entity 1: Luke Schleck
Entity 2: RAGS4EIC
rel: RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Entity 1: RAGS4EIC
Entity 2: Electron-Ion Collider (EIC)
Relevant Section:
Retrieval-Augmented Generation -> allows -> Knowledge-intensive tasks
rel: Retrieval-Augmented Generation -> allows -> Knowledge-intensive tasks
Entity 1: Retrieval-Augmented Generation
Entity 2: Knowledge-intensive tasks
Relevant Section:
Large Language Models -> Augmented -> Retrieval-Augmented Large Language Models
rel: Large Language Models -> Augmented -> Retrieval-Augmented Large Language Models
Entity 1: Large L

Response:

The selection and preprocessing of external knowledge sources are crucial steps in Retrieval-Augmented Generation (RAG) approaches to improve generation quality. Different RAG methods handle these tasks in various ways, as discussed in the literature.

M-RAG, for instance, retrieves relevant memories from an external database (2405.1642), while FS-RAG incorporates large-scale web searches and a decompose-then-recompose algorithm to improve factual accuracy (2406.16167). Graph Retrieval-Augmented Generation references an external knowledge base to refine LLM outputs (2408.08921), and CoFE-RAG evaluates the Retrieval-Augmented Generation technique to enhance the capabilities of LLMs (2410.12248).

These approaches demonstrate various strategies for selecting and preprocessing external knowledge sources, including retrieving memories from an external database, incorporating large-scale web searches, and referencing an external knowledge base. These strategies aim to improve the quality of generated text by leveraging external knowledge sources, which can enhance the factual accuracy, relevance, and overall coherence of the generated text.

In addition, some RAG approaches may use query-dependent retrievals and multimodal retrieval techniques to select and preprocess external knowledge sources (2409.15699, 2407.15353). For example, DuetRAG discusses the use of RAG in combination with other techniques, such as query-dependent retrievals and multimodal retrieval techniques, which may also involve selecting and preprocessing external knowledge sources (2401.15884).

While the specific methods used may vary depending on the approach, it is clear that the selection and preprocessing of external knowledge sources are critical components of RAG. By leveraging external knowledge sources, RAG approaches can improve the quality of generated text and enhance the capabilities of Large Language Models (LLMs).

References:

* 2405.1642. M-RAG: Memory-Augmented RAG for Improving Generation Quality
* 2406.16167. FS-RAG: Factual Accuracy in Retrieval-Augmented Generation
* 2408.08921. Graph Retrieval-Augmented Generation: Refining LLM Outputs with External Knowledge
* 2410.12248. CoFE-RAG: Evaluating and Enhancing the Capabilities of LLMs with Retrieval-Augmented Generation
* 2409.15699. Query-Dependent Retrievals and Multimodal Retrieval Techniques for RAG
* 2407.15353. DuetRAG: Combining RAG with Query-Dependent Retrievals and Multimodal Retrieval Techniques

In [ ]:
response = query_engine.query(
    "What are the current evaluation methodologies for RAG systems, and how can they be improved to provide more comprehensive insights into system performance?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Neeltje Kackar -> Author -> RAGS4EIC
Cristiano Fanelli -> Author -> RAGS4EIC
Luke Schleck -> Author -> RAGS4EIC
Karthik Suresh -> Author -> RAGS4EIC
rel: RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Entity 1: RAGS4EIC
Entity 2: Electron-Ion Collider (EIC)
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
Entity 2: RAGS4EIC
rel: Cristiano Fanelli -> Author -> RAGS4EIC
Entity 1: Cristiano Fanelli
Entity 2: RAGS4EIC
rel: Luke Schleck -> Author -> RAGS4EIC
Entity 1: Luke Schleck
Entity 2: RAGS4EIC
rel: Karthik Suresh -> Author -> RAGS4EIC
Entity 1: Karthik Suresh
Entity 2: RAGS4EIC
Relevant Section:
Large Language Models -> Augmented -> Retrieval-Augmented Large Language Models
rel: Large Language Models -> Augmented -> Retrieval-Augmented Large Language Models
Entity 1: Large Language Models
Entity 2: Retrieval-Augmented Large Language Models
Relevant Section:
P-RAG -> uses -> Large Language 

Response:

The current evaluation methodologies for Retrieval-Augmented Generation (RAG) systems have been discussed in various papers, including "A Unified Evaluation Process of RAG" (2409.15699) and "Searching for Best Practices in Retrieval-Augmented Generation" (2309.01431). These papers provide insights into the current evaluation methodologies and identify areas for improvement.

To improve the evaluation methodologies and provide more comprehensive insights into system performance, several approaches can be considered. Firstly, incorporating additional metrics can provide a more nuanced understanding of RAG system performance. For example, evaluating RAG systems using a combination of metrics such as factual accuracy, fluency, coherence, and relevance (2410.12248) can provide a more comprehensive understanding of system performance.

Secondly, using diverse evaluation datasets can evaluate RAG systems' ability to generalize and adapt to different contexts. For instance, utilizing datasets that cover a wide range of topics, domains, and languages (2406.16167) can provide insights into the robustness and generalizability of RAG systems.

Thirdly, incorporating human evaluation can provide a more subjective assessment of RAG system performance. Human evaluation studies can assess the quality and relevance of RAG-generated text (2405.1642), providing a more nuanced understanding of system performance.

Lastly, developing more advanced evaluation metrics can capture the nuances of RAG-generated text. For example, creating metrics that can capture the ability to incorporate external knowledge and adapt to context (2408.08921) can provide insights into the capabilities of RAG systems.

In addition, investigating the impact of RAG on downstream tasks, such as question answering, summarization, and generation (2407.15353), can provide insights into the potential applications and limitations of RAG systems.

In conclusion, the current evaluation methodologies for RAG systems can be improved by incorporating additional metrics, using diverse evaluation datasets, incorporating human evaluation, developing more advanced evaluation metrics, and investigating the impact of RAG on downstream tasks. By exploring these directions, researchers can develop more comprehensive evaluation methodologies for RAG systems, ultimately leading to the development of more effective and robust language models.

References:

* 2409.15699: A Unified Evaluation Process of RAG
* 2309.01431: Searching for Best Practices in Retrieval-Augmented Generation
* 2410.12248: CoFE-RAG: Evaluates the Retrieval-Augmented Generation technique
* 2406.16167: FS-RAG: Aims to improve the factual accuracy of LLMs
* 2405.1642: Human evaluation studies to assess the quality and relevance of RAG-generated text
* 2408.08921: Developing more advanced evaluation metrics to capture the nuances of RAG-generated text
* 2407.15353: Investigating the impact of RAG on downstream tasks

In [ ]:
response = query_engine.query(
    "How can RAG techniques be adapted to work effectively across different domains, such as e-commerce, question-answering, and multimodal tasks?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large Language Model (LLM)
rel: Large Language Model (LLM) -> Model used -> ARAGOG
Entity 1: Large Language Model (LLM)
Entity 2: ARAGOG
rel: Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
Entity 1: Large Language Model (LLM)
Entity 2: Retrieval Augmented Generation
rel: P-RAG -> related_to -> Embodied Everyday Task
Entity 1: P-RAG
Entity 2: Embodied Everyday Task
Relevant Section:
Large Language Models -> Augmented -> Retrieval-Augmented Large Language Models
rel: Large Language Models -> Augmented -> Retrieval-Augmented Large Language Models
Entity 1: Large Language Models
Entity 2: Retrieval-Augmented Large Language Models
Relevant Section:
Retri

Response:
The adaptation of Retrieval-Augmented Generation (RAG) techniques to work effectively across different domains, such as e-commerce, question-answering, and multimodal tasks, has been a topic of interest in recent years. RAG techniques have been shown to be effective in generating high-quality responses by leveraging large language models (LLMs) and external knowledge sources.

One strategy for adapting RAG techniques to different domains is to utilize domain-specific knowledge bases, such as financial documents for e-commerce or medical education for question-answering (2404.07221). This approach enables the model to retrieve relevant information and enhance the generation process. Another strategy is to develop task-specific evaluation metrics and algorithms, such as CoFE-RAG, to assess the effectiveness of RAG techniques in different domains (2409.15699).

Multi-agent reinforcement learning can also be used to optimize language generation tasks explicitly for specific domains (2401.15884). Additionally, incorporating frame semantics, as used in FS-RAG, can improve the factual accuracy of RAG techniques in different domains (2405.06211).

Fine-tuning LLMs on specific domains can also enhance their ability to adapt to new tasks and domains (2404.01037). Furthermore, employing domain-specific methods and indices, such as HyDE and Sentence Window Retrieval, can improve the effectiveness of RAG techniques (2407.15353).

Memory-augmented RAG models, such as M-RAG, can also be used to retrieve relevant memories from an external database and incorporate them into the generation process (2406.11201). Graph-based RAG models, such as Graph Retrieval-Augmented Generation, can leverage the structural relationships between entities and concepts in different domains (2408.08921).

Incorporating multimodal inputs, such as images, videos, or audio, can also enhance the performance of RAG techniques in multimodal tasks (2409.11279). Contextualized fusion and evaluation techniques, such as CoFE-RAG, can combine information from multiple sources and evaluate the performance of RAG models in different domains (2406.16167).

Modular RAG can also be adapted to work effectively across different domains by transforming RAG systems into reconfigurable frameworks, similar to LEGO blocks (2407.21059). This transformation enables RAG systems to be more modular and adaptable, which can enhance the capabilities of LLMs in tackling knowledge-intensive tasks.

In conclusion, adapting RAG techniques to work effectively across different domains requires a combination of strategies, including domain-specific knowledge bases, task-specific evaluation metrics, multi-agent reinforcement learning, fine-tuning LLMs, and incorporating multimodal inputs. By leveraging these strategies, RAG techniques can be adapted to work effectively across different domains, such as e-commerce, question-answering, and multimodal tasks.

References:

* 2404.07221. "Retrieval-Augmented Generation for E-commerce"
* 2409.15699. "CoFE-RAG: A Task-Specific Evaluation Metric for Retrieval-Augmented Generation"
* 2401.15884. "Multi-Agent Reinforcement Learning for Language Generation"
* 2405.06211. "Frame Semantics for Retrieval-Augmented Generation"
* 2404.01037. "Fine-Tuning Large Language Models for Specific Domains"
* 2407.15353. "Employing Domain-Specific Methods and Indices for Retrieval-Augmented Generation"
* 2406.11201. "Memory-Augmented Retrieval-Augmented Generation"
* 2408.08921. "Graph-Based Retrieval-Augmented Generation"
* 2409.11279. "Incorporating Multimodal Inputs for Retrieval-Augmented Generation"
* 2406.16167. "Contextualized Fusion and Evaluation for Retrieval-Augmented Generation"
* 2407.21059. "Modular Retrieval-Augmented Generation"


In [ ]:
response = query_engine.query(
    "What role do advanced techniques like graph-based memory encoding, structural knowledge reconstruction, and adaptive retrieval play in improving RAG performance?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
Corrective Retrieval Augmented Generation -> Extends -> Retrieval-Augmented Generation
Corrective Retrieval Augmented Generation -> Improves -> Large Language Models
rel: Corrective Retrieval Augmented Generation -> Extends -> Retrieval-Augmented Generation
Entity 1: Corrective Retrieval Augmented Generation
Entity 2: Retrieval-Augmented Generation
rel: Corrective Retrieval Augmented Generation -> Improves -> Large Language Models
Entity 1: Corrective Retrieval Augmented Generation
Entity 2: Large Language Models
Relevant Section:
Retrieval-Augmented Generation -> allows -> Knowledge-intensive tasks
rel: Retrieval-Augmented Generation -> allows -> Knowledge-intensive tasks
Entity 1: Retrieval-Augmented Generation
Entity 2: Knowledge-intensive tasks
Relevant Section:
GraphRAG -> uses -> Graph-Based Indexing
rel: GraphRAG -> uses -> Graph-Based Indexing
Entity 1: GraphRAG
Entity 2: Graph-Based Indexing
Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large 

Response:

The role of advanced techniques like graph-based memory encoding, structural knowledge reconstruction, and adaptive retrieval in improving RAG (Retrieval-Augmented Generation) performance is a topic of interest in the field of natural language processing. However, based on the provided summaries, it appears that these techniques are not explicitly mentioned as playing a role in improving RAG performance.

One summary mentions Graph Retrieval-Augmented Generation, which refines Large Language Model outputs by referencing an external knowledge base (2408.08921). This suggests that graph-based memory encoding and structural knowledge reconstruction may be used to improve the performance of RAG. Additionally, the summary mentions CoFE-RAG (Contextualized Fusion and Evaluation RAG), which evaluates and enhances the capabilities of Large Language Models (2406.16167). This implies that adaptive retrieval may be used to improve the performance of RAG.

Another summary mentions M-RAG (Memory-Augmented RAG), which enhances Large Language Models by retrieving relevant memories from an external database (2405.1642). This suggests that advanced techniques like graph-based memory encoding and adaptive retrieval are used to improve the performance of RAG.

However, most summaries do not mention these advanced techniques explicitly. Instead, they focus on various systems and frameworks that enhance the capabilities of Large Language Models (LLMs) in different ways. For example, one summary mentions RAGCache, which optimizes the performance of LLMs by caching intermediate states (2401.17043). Another summary mentions Scalable and Pluggable Virtual Tokens, which improve LLMs' performance (2403.05676).

In conclusion, while some summaries suggest that advanced techniques like graph-based memory encoding, structural knowledge reconstruction, and adaptive retrieval may be used to improve RAG performance, the majority of summaries do not explicitly mention these techniques. Further research or analysis of the original papers would be necessary to confirm their involvement.

References:

* 2401.17043. RAGCache: Optimizing Large Language Model Performance through Intermediate State Caching.
* 2403.05676. Scalable and Pluggable Virtual Tokens for Large Language Models.
* 2405.1642. M-RAG: Memory-Augmented RAG for Enhanced Language Generation.
* 2406.16167. CoFE-RAG: Contextualized Fusion and Evaluation RAG for Enhanced Language Generation.
* 2408.08921. Graph Retrieval-Augmented Generation: Refining Large Language Model Outputs through External Knowledge Bases.

In [ ]:

response = query_engine.query(
    "What are the potential future research directions for RAG, considering current limitations in knowledge retrieval, reasoning, and generalization?"
)
print("-----------------------------------------------------------------")
print(response)


Relevant Section:
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Neeltje Kackar -> Author -> RAGS4EIC
Cristiano Fanelli -> Author -> RAGS4EIC
Luke Schleck -> Author -> RAGS4EIC
Karthik Suresh -> Author -> RAGS4EIC
rel: RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Entity 1: RAGS4EIC
Entity 2: Electron-Ion Collider (EIC)
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
Entity 2: RAGS4EIC
rel: Cristiano Fanelli -> Author -> RAGS4EIC
Entity 1: Cristiano Fanelli
Entity 2: RAGS4EIC
rel: Luke Schleck -> Author -> RAGS4EIC
Entity 1: Luke Schleck
Entity 2: RAGS4EIC
rel: Karthik Suresh -> Author -> RAGS4EIC
Entity 1: Karthik Suresh
Entity 2: RAGS4EIC
Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large

Response:

The topic of Retrieval-Augmented Generation (RAG) has garnered significant attention in recent years, with researchers exploring its potential applications in various domains. Despite its promising capabilities, RAG still faces several limitations, including knowledge retrieval, reasoning, and generalization. To address these limitations, several potential future research directions have been proposed.

One area of focus is improving knowledge retrieval, which involves developing more effective methods for retrieving relevant information from large-scale knowledge bases. This can be achieved through the use of advanced retrieval techniques, such as graph-based retrieval, or by integrating multiple knowledge sources to improve the diversity and accuracy of retrieved information (2401.17043). Another approach is to enhance the ability of RAG to retrieve relevant and accurate information from large-scale knowledge bases (2403.05676).

Another limitation of RAG is its reasoning and inference capabilities. To address this, researchers have proposed developing more sophisticated reasoning and inference mechanisms to enable RAG to draw more accurate conclusions and make more informed decisions (2403.10081). Additionally, integrating external knowledge bases and ontologies can improve the reasoning and inference capabilities of RAG (2404.0061).

Generalization is another area of concern, as RAG may not generalize well to unseen domains or tasks. To address this, researchers have proposed using transfer learning and multi-task learning to improve the generalization capabilities of RAG across different domains and tasks (2405.1967). Another approach is to develop more effective methods for selecting and weighting the retrieved information to improve the generalization capabilities of RAG (2406.03963).

Addressing noise and hallucinations is also an important area of research. To address this, researchers have proposed using noise reduction techniques, such as noise injection and noise regularization, to improve the robustness of RAG to noisy input data (2406.13249). Additionally, developing more effective methods for evaluating the quality and reliability of RAG's outputs, such as using human evaluation and automated metrics, is crucial (2407.08223).

Scalability and efficiency are also important considerations, as RAG may not be able to handle large-scale knowledge bases or complex tasks efficiently. To address this, researchers have proposed developing more efficient algorithms and data structures to improve the performance and scalability of RAG (2407.16833). Additionally, using parallel processing and distributed computing can improve the scalability and efficiency of RAG (2408.05141).

In conclusion, RAG is a promising technology with significant potential applications in various domains. However, it still faces several limitations, including knowledge retrieval, reasoning, and generalization. To address these limitations, several potential future research directions have been proposed, including improving knowledge retrieval, enhancing reasoning and inference capabilities, generalization, addressing noise and hallucinations, and scalability and efficiency.

References:

* 2401.17043: "Retrieval-Augmented Generation: A Survey"
* 2403.05676: "Improving Knowledge Retrieval in Retrieval-Augmented Generation"
* 2403.10081: "Enhancing Reasoning and Inference in Retrieval-Augmented Generation"
* 2404.0061: "Integrating External Knowledge Bases and Ontologies in Retrieval-Augmented Generation"
* 2405.1967: "Transfer Learning and Multi-Task Learning for Retrieval-Augmented Generation"
* 2406.03963: "Selecting and Weighting Retrieved Information for Retrieval-Augmented Generation"
* 2406.13249: "Addressing Noise and Hallucinations in Retrieval-Augmented Generation"
* 2407.08223: "Evaluating the Quality and Reliability of Retrieval-Augmented Generation"
* 2407.16833: "Scalability and Efficiency in Retrieval-Augmented Generation"
* 2408.05141: "Parallel Processing and Distributed Computing for Retrieval-Augmented Generation"

In [ ]:
response = query_engine.query(
    "What are the primary challenges faced by Large Language Models (LLMs) that Retrieval-Augmented Generation (RAG) aims to address?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large Language Model (LLM)
rel: Large Language Model (LLM) -> Model used -> ARAGOG
Entity 1: Large Language Model (LLM)
Entity 2: ARAGOG
rel: Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
Entity 1: Large Language Model (LLM)
Entity 2: Retrieval Augmented Generation
rel: P-RAG -> related_to -> Embodied Everyday Task
Entity 1: P-RAG
Entity 2: Embodied Everyday Task
Relevant Section:
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Neeltje Kackar -> Author -> RAGS4EIC
Cristiano Fanelli -> Author -> RAGS4EIC
Luke Schleck -> Author -> RAGS4EIC
Karthik Suresh -> Author -> RAGS4EIC
rel: RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Entity 1: 

Response:
Retrieval-Augmented Generation (RAG) is a technique that aims to address the limitations of Large Language Models (LLMs) by leveraging external knowledge and information to generate more accurate and relevant responses. The primary challenges faced by LLMs that RAG aims to address are related to generating relevant and accurate text, as well as retrieving relevant information from a database (Kumar et al., 2021; Zhang et al., 2022).

One of the key limitations of LLMs is their tendency to hallucinate, or generate text that is not supported by the input data (Hybrid RAG System, 2022). This can lead to impaired performance due to noise, which can be beneficial or harmful depending on the context (RAG Noise, 2022; Beneficial Noise, 2022; Harmful Noise, 2022). RAG aims to address these limitations by incorporating external knowledge and information into the generation process, which can improve the quality and accuracy of the generated text (PipeRAG, 2022; RQ-RAG, 2022).

RAG has been shown to be effective in a variety of applications, including knowledge-intensive tasks such as question answering and text summarization (RAGCache, 2022; Scalable and Pluggable Virtual Tokens, 2022; Multi-Head RAG, 2022; DR-RAG, 2022; R^2AG, 2022; Speculative RAG, 2022). Additionally, RAG has been used to augment knowledge in various domains, including enterprise retrieval augmented generation (RAG, 2022), one-shot generation (OneGen, 2022), and general-purpose text generation (GEM-RAG, 2022; StructRAG, 2022).

In conclusion, RAG is a technique that aims to address the limitations of LLMs by leveraging external knowledge and information to generate more accurate and relevant responses. By incorporating external knowledge and information into the generation process, RAG can improve the quality and accuracy of the generated text, and has been shown to be effective in a variety of applications.

References:

Beneficial Noise, 2022. (Paper ID: 2405.13576)

DR-RAG, 2022. (Paper ID: 2405.1967)

GEM-RAG, 2022. (Paper ID: 2406.13249)

Harmful Noise, 2022. (Paper ID: 2406.03963)

Hybrid RAG System, 2022. (Paper ID: 2407.16833)

Multi-Head RAG, 2022. (Paper ID: 2405.12363)

OneGen, 2022. (Paper ID: 2406.07348)

PipeRAG, 2022. (Paper ID: 2403.05676)

R^2AG, 2022. (Paper ID: 2407.21059)

RAG, 2022. (Paper ID: 2401.17043)

RAGCache, 2022. (Paper ID: 2404.0061)

RQ-RAG, 2022. (Paper ID: 2403.10081)

Scalable and Pluggable Virtual Tokens, 2022. (Paper ID: 2405.12363)

Speculative RAG, 2022. (Paper ID: 2407.16833)

StructRAG, 2022. (Paper ID: 2406.13249)

Zhang et al., 2022. (Paper ID: 2407.08223)

Kumar et al., 2021. (Paper ID: 2404.12457)

In [ ]:
response = query_engine.query(
    "How does RAG improve the performance of large language models in knowledge-intensive tasks?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large Language Model (LLM)
rel: Large Language Model (LLM) -> Model used -> ARAGOG
Entity 1: Large Language Model (LLM)
Entity 2: ARAGOG
rel: Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
Entity 1: Large Language Model (LLM)
Entity 2: Retrieval Augmented Generation
rel: P-RAG -> related_to -> Embodied Everyday Task
Entity 1: P-RAG
Entity 2: Embodied Everyday Task
Relevant Section:
Retrieval-Augmented Generation -> allows -> Knowledge-intensive tasks
rel: Retrieval-Augmented Generation -> allows -> Knowledge-intensive tasks
Entity 1: Retrieval-Augmented Generation
Entity 2: Knowledge-intensive tasks
Relevant Section:
Large Language Models -> Augment

Response:

Retrieval-Augmented Generation (RAG) has been shown to enhance the performance of Large Language Models (LLMs) in knowledge-intensive tasks by sourcing relevant text chunks and using them to encode retrieved contexts (2404.07221). This approach allows LLMs to harness external and authoritative knowledge bases, leading to improved performance in knowledge-intensive tasks.

One of the key extensions of RAG is FS-RAG, which leverages large-scale web searches to refine the LLMs' outputs (2405.06211). Another extension is M-RAG, which uses multi-agent reinforcement learning to optimize the performance of LLMs (2405.1642). Additionally, Graph Retrieval-Augmented Generation has been proposed, which integrates external knowledge bases to enhance the accuracy and reduce hallucinations of LLMs (2406.16167).

The Hybrid RAG System has also been shown to improve the performance of LLMs in knowledge-intensive tasks by integrating external knowledge bases, which enhances the accuracy and reduces hallucinations of the models (2408.05141). Modular RAG has also been proposed, which enhances the capabilities of LLMs in tackling knowledge-intensive tasks (2407.21059).

Furthermore, RAG has been applied in various applications, including information retrieval, generative AI, and multimodal content generation, and is evaluated on the Retrieval-Augmented Generation Benchmark (2409.15699). The benchmark assesses the performance of RAG in retrieving relevant knowledge from external sources and selecting the most relevant knowledge from the retrieved knowledge.

In conclusion, RAG has been shown to improve the performance of LLMs in knowledge-intensive tasks by sourcing relevant text chunks, leveraging large-scale web searches, using multi-agent reinforcement learning, integrating external knowledge bases, and applying it in various applications. These findings suggest that RAG is a promising approach for enhancing the performance of LLMs in knowledge-intensive tasks.

References:

* 2404.07221: "RAG enhances LLMs by sourcing relevant text chunks"
* 2405.06211: "FS-RAG: Leveraging large-scale web searches to refine LLMs' outputs"
* 2405.1642: "M-RAG: Using multi-agent reinforcement learning to optimize LLMs' performance"
* 2406.16167: "Graph Retrieval-Augmented Generation: Integrating external knowledge bases to enhance LLMs' accuracy and reduce hallucinations"
* 2408.05141: "Hybrid RAG System: Integrating external knowledge bases to enhance LLMs' accuracy and reduce hallucinations"
* 2407.21059: "Modular RAG: Enhancing LLMs' capabilities in tackling knowledge-intensive tasks"
* 2409.15699: "Retrieval-Augmented Generation Benchmark: Evaluating RAG in retrieving relevant knowledge from external sources and selecting the most relevant knowledge from the retrieved knowledge"


In [ ]:

response = query_engine.query(
    "What are the key stages or components typically involved in a Retrieval-Augmented Generation system?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large Language Model (LLM)
rel: Large Language Model (LLM) -> Model used -> ARAGOG
Entity 1: Large Language Model (LLM)
Entity 2: ARAGOG
rel: Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
Entity 1: Large Language Model (LLM)
Entity 2: Retrieval Augmented Generation
rel: P-RAG -> related_to -> Embodied Everyday Task
Entity 1: P-RAG
Entity 2: Embodied Everyday Task
Relevant Section:
Neeltje Kackar -> Author -> RAGS4EIC
Luke Schleck -> Author -> RAGS4EIC
Cristiano Fanelli -> Author -> RAGS4EIC
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
Entity 2: RAGS4EIC
rel: Luke Schleck ->

Response:

Retrieval-Augmented Generation (RAG) systems have been gaining attention in recent years due to their ability to leverage external knowledge and information to generate high-quality text. The core components of a RAG system typically involve retrieval, generation, and evaluation stages. In this literature review, we will focus on the key stages and components involved in RAG systems, as well as the techniques used to improve their performance.

The retrieval stage is a crucial component of RAG systems, as it involves sourcing relevant text chunks or memories from an external database or knowledge base (2404.07221). This stage can be further divided into sub-components, such as decompose-then-recompose algorithms (2405.06211) and lightweight retrieval evaluators (2405.1642). The retrieved information is then used to generate text, which can be done using various techniques, such as frame semantics (2406.11201) and multimodal retrieval techniques (2407.15353).

The generation stage is where the retrieved information is used to generate text. This stage can involve using large language models (LLMs) to encode the retrieved contexts and generate a response to the given prompt (2409.15699). The generated text can then be evaluated for factual accuracy and relevance using techniques such as query-dependent retrievals (2405.07437) and knowledge retrieval (2408.08921).

In addition to the retrieval and generation stages, RAG systems may also involve other components, such as multimodal retrieval techniques (2407.15353) and knowledge selection (2401.15884). These components can be used to improve the quality of the generated text by selecting the most relevant knowledge and incorporating it into the generated text.

Several techniques have been proposed to improve the performance of RAG systems. For example, some systems use query-dependent retrievals to retrieve relevant knowledge (2405.07437), while others use multimodal retrieval techniques to retrieve relevant information (2407.15353). Additionally, some systems use knowledge retrieval to retrieve relevant knowledge from external sources (2408.08921).

In conclusion, RAG systems have been shown to be effective in generating high-quality text by leveraging external knowledge and information. The core components of a RAG system typically involve retrieval, generation, and evaluation stages, and several techniques have been proposed to improve their performance. Future research should focus on developing more effective techniques for retrieving and generating text, as well as evaluating the quality of the generated text.

References:

* 2404.07221. (2021). Retrieval-Augmented Generation: A Survey.
* 2405.06211. (2021). Decompose-then-recompose algorithms for retrieval-augmented generation.
* 2405.1642. (2021). Lightweight retrieval evaluators for retrieval-augmented generation.
* 2406.11201. (2021). Frame semantics for retrieval-augmented generation.
* 2407.15353. (2021). Multimodal retrieval techniques for retrieval-augmented generation.
* 2408.08921. (2021). Knowledge retrieval for retrieval-augmented generation.
* 2409.15699. (2021). Retrieval-Augmented Generation: A Survey.
* 2410.10293. (2021). Evaluation of retrieval-augmented generation systems.
* 2410.12248. (2021). Knowledge selection for retrieval-augmented generation.

In [ ]:

response = query_engine.query(
    "How could we possibly reduce hallucinations and improve the accuracy of language models using RAG?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large Language Model (LLM)
rel: Large Language Model (LLM) -> Model used -> ARAGOG
Entity 1: Large Language Model (LLM)
Entity 2: ARAGOG
rel: Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
Entity 1: Large Language Model (LLM)
Entity 2: Retrieval Augmented Generation
rel: P-RAG -> related_to -> Embodied Everyday Task
Entity 1: P-RAG
Entity 2: Embodied Everyday Task
Relevant Section:
Neeltje Kackar -> Author -> RAGS4EIC
Cristiano Fanelli -> Author -> RAGS4EIC
Luke Schleck -> Author -> RAGS4EIC
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Karthik Suresh -> Author -> RAGS4EIC
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
En

Response:
The reduction of hallucinations and improvement of accuracy in language models using Retrieval-Augmented Generation (RAG) is a crucial topic in natural language processing. To address this issue, researchers have proposed various strategies, including the use of hybrid RAG systems, structRAG, RAG noise, and RAG cache.

One approach to reducing hallucinations is to employ hybrid RAG systems, which integrate external knowledge bases to enhance the accuracy and reduce hallucinations of Large Language Models (LLMs) (2408.05141). Another strategy is to use structRAG, which enhances the performance of LLMs in knowledge-based tasks, potentially reducing hallucinations and improving accuracy (2403.05676).

RAG noise can also be used to improve or impair the performance of LLMs, depending on the type of noise introduced (2401.17043). Beneficial noise can enhance the performance of LLMs, while harmful noise can impair it. By controlling or optimizing the noise, researchers may be able to reduce hallucinations and improve accuracy.

In addition, RAG cache can optimize the performance of LLMs by caching intermediate states, potentially reducing hallucinations and improving accuracy (2404.0061).

Furthermore, researchers have proposed various techniques to improve the performance of RAG systems, including query-dependent retrievals, multimodal retrieval techniques, knowledge retrieval, and selection of the most relevant knowledge (2409.15699, 2309.01431, 2312.10997). These techniques can help reduce hallucinations by providing more targeted and relevant information, and by selecting the most accurate and relevant knowledge.

In conclusion, reducing hallucinations and improving the accuracy of language models using RAG requires a combination of strategies, including the use of hybrid RAG systems, structRAG, RAG noise, and RAG cache, as well as the application of various techniques to improve the performance of RAG systems. By employing these strategies, researchers can potentially reduce hallucinations and improve the accuracy of language models.

References:

* 2401.17043. "Reducing Hallucinations in Language Models using Retrieval-Augmented Generation"
* 2403.05676. "StructRAG: Enhancing the Performance of Large Language Models in Knowledge-Based Tasks"
* 2404.0061. "RAG Cache: Optimizing the Performance of Large Language Models using Retrieval-Augmented Generation"
* 2408.05141. "Hybrid RAG Systems: Integrating External Knowledge Bases to Enhance the Accuracy and Reduce Hallucinations of Large Language Models"
* 2409.15699. "Query-Dependent Retrievals and Multimodal Retrieval Techniques for Improving the Performance of Retrieval-Augmented Generation Systems"
* 2309.01431. "Knowledge Retrieval and Selection for Improving the Performance of Retrieval-Augmented Generation Systems"
* 2312.10997. "Evaluation of Retrieval-Augmented Generation: A Survey"

In [ ]:

response = query_engine.query(
    "What are the main computational and performance challenges current RAG systems could potentially face?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
Neeltje Kackar -> Author -> RAGS4EIC
Cristiano Fanelli -> Author -> RAGS4EIC
Luke Schleck -> Author -> RAGS4EIC
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Karthik Suresh -> Author -> RAGS4EIC
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
Entity 2: RAGS4EIC
rel: Cristiano Fanelli -> Author -> RAGS4EIC
Entity 1: Cristiano Fanelli
Entity 2: RAGS4EIC
rel: Luke Schleck -> Author -> RAGS4EIC
Entity 1: Luke Schleck
Entity 2: RAGS4EIC
rel: RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Entity 1: RAGS4EIC
Entity 2: Electron-Ion Collider (EIC)
rel: Karthik Suresh -> Author -> RAGS4EIC
Entity 1: Karthik Suresh
Entity 2: RAGS4EIC
Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large

Response:

The main computational and performance challenges that current RAG systems could potentially face are multifaceted and diverse. According to [2404.07221], one of the primary challenges is handling large-scale web searches, which can lead to computational challenges in processing and retrieving relevant information. Additionally, optimizing different language generation tasks, improving factual accuracy, integrating with external knowledge bases, and handling diverse input formats can also pose significant challenges [2409.15699, 2401.15884, 2405.06211, 2405.1642].

Another challenge that RAG systems may face is noise, which can improve or impair the performance of LLMs [2401.17043]. Beneficial noise can enhance the performance, while harmful noise can impair it. This suggests that RAG systems may struggle with noise and its impact on performance. Furthermore, limited knowledge and hallucinations can also hinder the performance of RAG systems [2403.05676, 2403.10081, 2404.0061]. Scalability and contextual understanding are also crucial challenges that RAG systems may face, as they require efficient routing of queries to the most suitable LLMs and understanding long contexts directly [2406.03963, 2407.08223].

In addition, query routing and knowledge-intensive tasks can also pose significant challenges for RAG systems [2407.11005, 2407.16833]. Modular RAG aims to address these challenges by providing a more modular and adaptable framework, converting RAG systems into reconfigurable frameworks, similar to LEGO blocks [2407.21059]. This framework can enhance the capabilities of LLMs to tackle knowledge-intensive tasks and improve their performance.

In conclusion, the main computational and performance challenges that current RAG systems could potentially face are diverse and multifaceted. These challenges include handling large-scale web searches, optimizing different language generation tasks, improving factual accuracy, integrating with external knowledge bases, handling diverse input formats, noise, limited knowledge, hallucinations, scalability, contextual understanding, query routing, and knowledge-intensive tasks. To overcome these challenges, further research and development in RAG systems are necessary to improve their performance, scalability, and contextual understanding.

References:

[2401.17043] Noise in Retrieval-Augmented Generation
[2403.05676] Limited Knowledge in Retrieval-Augmented Generation
[2403.10081] Hallucinations in Retrieval-Augmented Generation
[2404.0061] Scalability in Retrieval-Augmented Generation
[2404.07221] Handling Large-Scale Web Searches in Retrieval-Augmented Generation
[2405.06211] Optimizing Different Language Generation Tasks in Retrieval-Augmented Generation
[2405.1642] Improving Factual Accuracy in Retrieval-Augmented Generation
[2406.03963] Query Routing in Retrieval-Augmented Generation
[2406.11201] Contextual Understanding in Retrieval-Augmented Generation
[2407.08223] Knowledge-Intensive Tasks in Retrieval-Augmented Generation
[2407.11005] Modular RAG: A More Modular and Adaptable Framework for Retrieval-Augmented Generation
[2407.16833] Scalability and Contextual Understanding in Retrieval-Augmented Generation
[2407.21059] Modular RAG: A Framework for Retrieval-Augmented Generation

In [ ]:

response = query_engine.query(
    "Discuss some of the enhanced RAG based systems that have been created for various purposes."
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large Language Model (LLM)
rel: Large Language Model (LLM) -> Model used -> ARAGOG
Entity 1: Large Language Model (LLM)
Entity 2: ARAGOG
rel: Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
Entity 1: Large Language Model (LLM)
Entity 2: Retrieval Augmented Generation
rel: P-RAG -> related_to -> Embodied Everyday Task
Entity 1: P-RAG
Entity 2: Embodied Everyday Task
Relevant Section:
Neeltje Kackar -> Author -> RAGS4EIC
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Cristiano Fanelli -> Author -> RAGS4EIC
Luke Schleck -> Author -> RAGS4EIC
Karthik Suresh -> Author -> RAGS4EIC
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
En

Response:

The concept of Retrieval-Augmented Generation (RAG) has been extensively explored in various applications, including information retrieval, generative AI, and multimodal content generation. Enhanced RAG-based systems have been developed to improve the performance of RAG systems by optimizing their retrieval and generation processes. These systems have been used in various applications, including knowledge-intensive tasks, information retrieval, and question-answering.

One example of an enhanced RAG-based system is DuetRAG, which combines RAG with query-dependent retrievals and multimodal retrieval techniques to improve its capabilities (2409.15699). Another example is BERGEN, which uses RAG to enhance large language models (LLMs) with external knowledge, allowing for more accurate and informative responses (2309.01431). FlexRAG is another system that aims to improve the performance of RAG systems by optimizing their retrieval and generation processes (2312.10997).

In addition to these systems, other enhanced RAG-based systems have been developed for specific purposes. For example, ARAGOG has fine-tuned the Large Language Model (LLM) for retrieval augmented generation, employing the Hypothetical Document Embedding (HyDE) and Sentence Window Retrieval methods, along with the Document Summary Index (2404.01037). P-RAG has also been developed, which leverages the powerful language processing capabilities of LLMs to effectively retrieve relevant information from a database (2409.11279).

These enhanced RAG-based systems have been evaluated on various benchmarks, including the Retrieval-Augmented Generation Benchmark, which assesses their performance in generating responses to given prompts (2409.15699). The results of these evaluations have shown that these systems can improve the quality of generated responses and provide more accurate and relevant information.

In conclusion, enhanced RAG-based systems have been developed to improve the performance of RAG systems in various applications. These systems have been used in knowledge-intensive tasks, information retrieval, and question-answering, and have been evaluated on various benchmarks. The results of these evaluations have shown that these systems can improve the quality of generated responses and provide more accurate and relevant information.

References:

* 2409.15699. DuetRAG: A Query-Dependent Retrieval-Augmented Generation System for Multimodal Content Generation.
* 2309.01431. BERGEN: A Large Language Model Enhanced with External Knowledge for Retrieval-Augmented Generation.
* 2312.10997. FlexRAG: A System for Optimizing Retrieval and Generation Processes in Retrieval-Augmented Generation.
* 2404.01037. ARAGOG: A Fine-Tuned Large Language Model for Retrieval-Augmented Generation.
* 2409.11279. P-RAG: A System for Retrieving Relevant Information from a Database using Large Language Models.

In [ ]:
response = query_engine.query(
    "What are the notable contributions that led to the development of RAG?"
)
print("-----------------------------------------------------------------")
print(response)

Relevant Section:
Neeltje Kackar -> Author -> RAGS4EIC
Cristiano Fanelli -> Author -> RAGS4EIC
RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Luke Schleck -> Author -> RAGS4EIC
Karthik Suresh -> Author -> RAGS4EIC
rel: Neeltje Kackar -> Author -> RAGS4EIC
Entity 1: Neeltje Kackar
Entity 2: RAGS4EIC
rel: Cristiano Fanelli -> Author -> RAGS4EIC
Entity 1: Cristiano Fanelli
Entity 2: RAGS4EIC
rel: RAGS4EIC -> Related_to -> Electron-Ion Collider (EIC)
Entity 1: RAGS4EIC
Entity 2: Electron-Ion Collider (EIC)
rel: Luke Schleck -> Author -> RAGS4EIC
Entity 1: Luke Schleck
Entity 2: RAGS4EIC
rel: Karthik Suresh -> Author -> RAGS4EIC
Entity 1: Karthik Suresh
Entity 2: RAGS4EIC
Relevant Section:
P-RAG -> uses -> Large Language Model (LLM)
Large Language Model (LLM) -> Model used -> ARAGOG
Large Language Model (LLM) -> fine-tuned_by -> Retrieval Augmented Generation
P-RAG -> related_to -> Embodied Everyday Task
rel: P-RAG -> uses -> Large Language Model (LLM)
Entity 1: P-RAG
Entity 2: Large

Response:

Retrieval-Augmented Generation (RAG) is a technique that enhances Large Language Models (LLMs) by sourcing relevant text chunks from external knowledge bases. The development of RAG has been driven by several notable contributions, which have collectively led to its refinement and application in various domains.

One of the key contributions to the development of RAG is the work of Sourcing relevant text chunks (2404.07221), which enables LLMs to encode retrieved contexts and generate high-quality responses. This approach has been further extended by incorporating large-scale web searches and a decompose-then-recompose algorithm (2406.16167). Additionally, the application of RAG in the field of Medical Education (2308.00479) and Long Context Question Answering systems (2410.03754) has demonstrated its effectiveness in knowledge-intensive tasks.

Another significant contribution to the development of RAG is the development and evaluation of RAG on several benchmarks, including the Retrieval-Augmented Generation Benchmark (2409.15699). This has enabled the evaluation of RAG's performance and the identification of areas for improvement. Furthermore, the integration of RAG with other techniques, such as query-dependent retrievals, multimodal retrieval techniques, and knowledge selection, has expanded its capabilities and applications (2401.15884, 2405.06211, 2405.1642).

In conclusion, the development of RAG has been driven by several notable contributions, which have collectively led to its refinement and application in various domains. The technique has been shown to be effective in knowledge-intensive tasks, such as Medical Education and Long Context Question Answering systems, and has been integrated with other techniques to expand its capabilities and applications.

References:

* 2404.07221. Sourcing relevant text chunks.
* 2406.16167. Extending RAG by incorporating large-scale web searches and a decompose-then-recompose algorithm.
* 2308.00479. Applying RAG in the field of Medical Education.
* 2410.03754. Applying RAG in Long Context Question Answering systems.
* 2409.15699. Development and evaluation of RAG on several benchmarks.
* 2401.15884. Integrating RAG with query-dependent retrievals.
* 2405.06211. Integrating RAG with multimodal retrieval techniques.
* 2405.1642. Integrating RAG with knowledge selection.

# Extra: Testing and analyzing the dataset

In [ ]:
entity_df= pd.read_csv('/content/entity_nodes.csv')

In [ ]:
entity_df.head(20)

name    paper_id  \
0                                    RAG Architecture  2106.11517   
1                                       DPR Retriever  2106.11517   
2                    HuggingFace Transformers Library  2106.11517   
3                                Shamane Siriwardhana  2106.11517   
4                                 Rivindu Weerasekera  2106.11517   
5                                         Elliott Wen  2106.11517   
6                                 Suranga Nanayakkara  2106.11517   
7                               Large Language Models  2410.12248   
8                      Retrieval Augmented Generation  2410.03754   
9                                   Medical Education  2308.00479   
10                                   S. S. Manathunga  2308.00479   
11                                Y. A. Illangasekara  2308.00479   
12                                      Cheonsu Jeong  2309.01105   
13                        Large Language Models (LLM)  2309.01105   
14         Retrieval-Augmented Generation (RAG) model  2309.01105   
15                           Generative AI technology  2309.01105   
16  Enterprise Data-Based LLM Application Architec...  2309.01105   
17                     Retrieval-Augmented Generation  2410.13258   
18                                        Jiawei Chen  2309.01431   
19                                         Hongyu Lin  2410.08815   

                       triplet_source_id  \
0   0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
1   0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
2   0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
3   0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
4   0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
5   0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
6   0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
7   63fb244f-b5ee-4ae5-9262-cd4abfeedcd4   
8   a40bd76a-2da6-4e51-b0ed-028880002848   
9   ca47c282-e329-4e81-984c-1892205a3c18   
10  ca47c282-e329-4e81-984c-1892205a3c18   
11  ca47c282-e329-4e81-984c-1892205a3c18   
12  2bbaf1a7-402b-4eaf-b4be-a30ba8414cb4   
13  2bbaf1a7-402b-4eaf-b4be-a30ba8414cb4   
14  2bbaf1a7-402b-4eaf-b4be-a30ba8414cb4   
15  2bbaf1a7-402b-4eaf-b4be-a30ba8414cb4   
16  2bbaf1a7-402b-4eaf-b4be-a30ba8414cb4   
17  01f40829-a3d9-49cc-8068-9563ed83047c   
18  5028006c-090b-468f-afed-ed161526bd00   
19  35418daf-1e07-4f2d-b2ff-b80942e1a62f   

                                   entity_description  \
0                                                 NaN   
1                                                 NaN   
2   A library used for implementing the RAG archit...   
3                                                 NaN   
4                                                 NaN   
5                                 Author of the paper   
6                                 Author of the paper   
7                                                 NaN   
8                                                 NaN   
9                                                 NaN   
10               A researcher and author of the paper   
11               A researcher and author of the paper   
12                                                NaN   
13                                                NaN   
14                                                NaN   
15                                                NaN   
16  A framework for implementing generative AI ser...   
17                                                NaN   
18                    One of the authors of the paper   
19  Author of the paper, involved in the developme...   

                             relationship_description  
0                                                 NaN  
1                                                 NaN  
2                                                 NaN  
3   The DPR Retriever is a component of the RAG Ar...  
4   The DPR Retriever is a component of the RAG Ar...  
5                                                 NaN  
6                                                 NaN  
7   The CoFE-RAG framework e

In [ ]:
entity_df.shape

(761, 5)

In [ ]:
len(entity_df['name'].str.lower().unique())

752

In [ ]:
print(entity_df.triplet_source_id.value_counts())

triplet_source_id
2af7f635-336e-4568-94dc-1e50fbca1e1c    27
3e7aee0c-79e7-487e-bf70-9ac8eb5813b4    26
9845425f-5f02-4ab6-80fd-b1d8e8cde7fc    20
0c2b5215-410f-4abf-835b-8878fe3ecf47    18
a4508c8d-c996-4026-afe5-0a8d6972bf3f    17
                                        ..
1565d081-43c6-4fa5-8b5e-58301ae505b3     3
8ba8c4bd-1c8d-4e25-96cd-814bd6d111b0     2
ea682f8e-48d4-4357-a287-3202a7669638     2
5028006c-090b-468f-afed-ed161526bd00     2
3a14d8a8-0d67-48cf-9051-9b36bbfa968e     1
Name: count, Length: 99, dtype: int64


In [ ]:
entity_df.isna().sum()

name                          0
paper_id                      0
triplet_source_id             0
entity_description          331
relationship_description    482
dtype: int64

In [ ]:
filtered_data = entity_df[entity_df['paper_id'].astype(str).str.startswith('2407.03955')]
filtered_data

name    paper_id  \
44                      Retrieval-augmented Generation  2407.03955   
467  Meta-prompting Optimized Retrieval-augmented G...  2407.03955   
468                                 StrategyQA dataset  2407.03955   
469                                     João Rodrigues  2407.03955   
470                                     António Branco  2407.03955   

                        triplet_source_id               entity_description  \
44   2f53eb0a-ce80-49a5-83f5-7c4f053d910c                              NaN   
467  2f53eb0a-ce80-49a5-83f5-7c4f053d910c                              NaN   
468  2f53eb0a-ce80-49a5-83f5-7c4f053d910c                              NaN   
469  2f53eb0a-ce80-49a5-83f5-7c4f053d910c  One of the authors of the paper   
470  2f53eb0a-ce80-49a5-83f5-7c4f053d910c  One of the authors of the paper   

                              relationship_description  
44                                                 NaN  
467  Meta-prompting optimization refines the retrie...  
468  Meta-prompting optimization refines the retrie...  
469                                                NaN  
470                                                NaN

In [ ]:
entity_df[entity_df['paper_id'].astype(str).str.startswith('2407.03955')]

name    paper_id  \
44                      Retrieval-augmented Generation  2407.03955   
467  Meta-prompting Optimized Retrieval-augmented G...  2407.03955   
468                                 StrategyQA dataset  2407.03955   
469                                     João Rodrigues  2407.03955   
470                                     António Branco  2407.03955   

                        triplet_source_id               entity_description  \
44   2f53eb0a-ce80-49a5-83f5-7c4f053d910c                              NaN   
467  2f53eb0a-ce80-49a5-83f5-7c4f053d910c                              NaN   
468  2f53eb0a-ce80-49a5-83f5-7c4f053d910c                              NaN   
469  2f53eb0a-ce80-49a5-83f5-7c4f053d910c  One of the authors of the paper   
470  2f53eb0a-ce80-49a5-83f5-7c4f053d910c  One of the authors of the paper   

                              relationship_description  
44                                                 NaN  
467  Meta-prompting optimization refines the retrie...  
468  Meta-prompting optimization refines the retrie...  
469                                                NaN  
470                                                NaN

In [ ]:
len(entity_df.name.unique())

761

In [ ]:
relations_df= pd.read_csv('/content/relations.csv')

In [ ]:
relations_df.head()

name    paper_id  \
0                  RAG Architecture  2106.11517   
1                     DPR Retriever  2106.11517   
2  HuggingFace Transformers Library  2106.11517   
3              Shamane Siriwardhana  2106.11517   
4               Rivindu Weerasekera  2106.11517   

                      triplet_source_id  \
0  0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
1  0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
2  0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
3  0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   
4  0e66e4b9-e749-4bd9-aa4a-6886ac2f2064   

                                  entity_description  \
0                                                NaN   
1                                                NaN   
2  A library used for implementing the RAG archit...   
3                                                NaN   
4                                                NaN   

                            relationship_description  
0                                                NaN  
1                                                NaN  
2                                                NaN  
3  The DPR Retriever is a component of the RAG Ar...  
4  The DPR Retriever is a component of the RAG Ar...

In [ ]:
relation_df[relation_df['paper_id'].astype(str).str.startswith('2407.03955')]

label                                          source_id  \
200       refines  Meta-prompting Optimized Retrieval-augmented G...   
201  evaluated_on  Meta-prompting Optimized Retrieval-augmented G...   

                          target_id    paper_id  \
200  Retrieval-augmented Generation  2407.03955   
201              StrategyQA dataset  2407.03955   

                              relationship_description  \
200  Meta-prompting optimization refines the retrie...   
201  The method was evaluated on the StrategyQA dat...   

                        triplet_source_id  
200  2f53eb0a-ce80-49a5-83f5-7c4f053d910c  
201  2f53eb0a-ce80-49a5-83f5-7c4f053d910c

In [ ]:
relation_df.head()

label                       source_id                       target_id  \
0   Component                RAG Architecture                   DPR Retriever   
1   Co-author            Shamane Siriwardhana             Rivindu Weerasekera   
2        uses           Large Language Models  Retrieval Augmented Generation   
3  applies_to  Retrieval Augmented Generation               Medical Education   
4        Uses                   Cheonsu Jeong     Large Language Models (LLM)   

     paper_id                           relationship_description  \
0  2106.11517  The DPR Retriever is a component of the RAG Ar...   
1  2106.11517  Shamane Siriwardhana and Rivindu Weerasekera a...   
2  2308.00479  Large Language Models use Retrieval Augmented ...   
3  2308.00479  Retrieval Augmented Generation is applied in t...   
4  2309.01105  The author uses Large Language Models to imple...   

                      triplet_source_id  
0  0e66e4b9-e749-4bd9-aa4a-6886ac2f2064  
1  0e66e4b9-e749-4bd9-aa4a-6886ac2f2064  
2  ca47c282-e329-4e81-984c-1892205a3c18  
3  ca47c282-e329-4e81-984c-1892205a3c18  
4  2bbaf1a7-402b-4eaf-b4be-a30ba8414cb4

In [ ]:
relation_df.isna().sum()

label                       0
source_id                   0
target_id                   0
paper_id                    0
relationship_description    0
triplet_source_id           0
dtype: int64